In [3]:
#!/usr/bin/python
# -*- coding: utf-8 -*-
# ========== python ==========
import os
from logging import Logger
from pathlib import Path
import gc
# noinspection PyUnresolvedReferences
from typing import List, Dict, Tuple, Optional, Union, Callable, Final, Literal, get_args
import torch
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
PROJECT_DIR = Path().resolve().parents[0]
os.chdir(PROJECT_DIR)
SEED: Final = 42


In [4]:
from utils.setup import load_param, easy_logger, get_device
from utils.torch import load_model, torch_fix_seed
from torch.utils.tensorboard.writer import SummaryWriter
from ignite.handlers import Checkpoint
from run_for_KGC import main_function
logger = easy_logger('log/test.log')

In [5]:
args = load_param('saved_models/1226/01/param.pkl')
device = get_device(device_name='cpu', logger=logger)
# args.pre_train = True
args.logger = logger
args.device = device
args.batch_size = 1
args.no_use_pe = False
args.max_len=512
args.tensorboard_dir=None
args.only_load_trainer_evaluator=True
args.pre_train=False
del args.optuna_file, args.device_name, args.pid
del args.study_name, args.n_trials
logger.info(args)

2022-12-28 15:43:26 - INFO - 2779299506.py - 14 - Namespace(notebook=False, train_anyway=False, logfile='saved_models/1226/01/log.log', param_file='saved_models/1226/01/param.pkl', tensorboard_dir=None, checkpoint_dir='saved_models/1226/01/checkpoint/', model_path='saved_models/1226/01/model.pth', model_version='03', resume_from_checkpoint=False, resume_from_last_point=False, only_load_trainer_evaluator=True, resume_checkpoint_path=None, console_level='info', pre_train=False, train_valid_test=True, only_train=False, use_for_challenge100=False, use_for_challenge075=False, use_title=None, do_optuna=False, story_special_num=5, relation_special_num=5, entity_special_num=5, padding_token_e=0, cls_token_e=1, mask_token_e=2, sep_token_e=3, bos_token_e=4, padding_token_r=0, cls_token_r=1, mask_token_r=2, sep_token_r=3, bos_token_r=4, padding_token_s=0, cls_token_s=1, mask_token_s=2, sep_token_s=3, bos_token_s=4, embedding_dim=128, entity_embedding_dim=128, relation_embedding_dim=64, separate_h

In [6]:
torch_fix_seed(seed=SEED)
model, data_dict = main_function(args, logger=logger)
encoder_last_layer = model.transformer.layers[-1]
model.eval()
dataset_train, dataset_valid, dataset_test = data_dict['datasets']
triple = dataset_train.triple
data_helper = data_dict['data_helper']
evaluator = data_dict['train_items']['evaluator']
load_model(model, args.model_path, device)

2022-12-28 15:43:29 - INFO - run_for_KGC.py - 730 - ----- make datahelper start. -----
2022-12-28 15:43:29 - INFO - data_helper.py - 438 - ==========Show DataHelper==========
2022-12-28 15:43:29 - INFO - data_helper.py - 439 - ==========
2022-12-28 15:43:29 - INFO - data_helper.py - 205 - ==========Show MyRawData==========
2022-12-28 15:43:29 - INFO - data_helper.py - 206 - entity_length: 7857
2022-12-28 15:43:29 - INFO - data_helper.py - 207 - relation_length: 63
2022-12-28 15:43:29 - INFO - data_helper.py - 210 - ==========Show MyRawData==========
2022-12-28 15:43:29 - INFO - data_helper.py - 441 - ==========
2022-12-28 15:43:29 - INFO - data_helper.py - 443 - entity_special_num: 5
2022-12-28 15:43:29 - INFO - data_helper.py - 444 - relation_special_num: 5
2022-12-28 15:43:29 - INFO - data_helper.py - 445 - ==========Show DataHelper==========
2022-12-28 15:43:29 - INFO - run_for_KGC.py - 732 - ----- make datahelper complete. -----
2022-12-28 15:43:29 - INFO - run_for_KGC.py - 735 - -

KgStoryTransformer03(
  (entity_embeddings): Embedding(7862, 128, padding_idx=0)
  (relation_embeddings): Embedding(68, 64, padding_idx=0)
  (pe): PositionalEncoding(
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (transformer): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=128, out_features=128, bias=True)
        )
        (linear1): Linear(in_features=128, out_features=1028, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
        (linear2): Linear(in_features=1028, out_features=128, bias=True)
        (norm1): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (norm2): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (dropout1): Dropout(p=0.1, inplace=False)
        (dropout2): Dropout(p=0.1, inplace=False)
        (activation): GELU(approximate='none')
      )
      (1): TransformerEncoderLayer(
      

In [7]:
entities = data_helper.processed_entities
d_e = {e: i for i, e in enumerate(entities)}
relations = data_helper.processed_relations
d_r = {r: i for i, r in enumerate(relations)}
triple_df = pd.DataFrame([(entities[_t[0]], relations[_t[1]], entities[_t[2]]) for _t in triple], columns=['head', 'relation', 'tail']) 
# story_entities = triple_df
# triple_df

In [8]:
def extract(model, target, inputs):
    feature = None

    def forward_hook(module, inputs, _):
        # 順伝搬の出力を features というグローバル変数に記録する
        global features
        # 1. detach でグラフから切り離す。
        # 2. clone() でテンソルを複製する。モデルのレイヤーで ReLU(inplace=True) のように
        #    inplace で行う層があると、値がその後のレイヤーで書き換えられてまい、
        #    指定した層の出力が取得できない可能性があるため、clone() が必要。
        x, _, _ = inputs
        outputs = module.forward(x, x, x, need_weights=True)[1]
        features = outputs.detach().clone()

    # コールバック関数を登録する。
    handle = target.register_forward_hook(forward_hook)

    # 推論する
    model.eval()
    model(inputs, torch.LongTensor([[]]), torch.LongTensor([[]]), torch.LongTensor([[]]))

    # コールバック関数を解除する。
    handle.remove()

    return features

In [9]:
def heatmap_(index):
    input_ = dataset[index]
    # display([(i, entities[h], relations[r], entities[t]) for i, (h, r, t) in enumerate(input_)])
    features = extract(model, encoder_last_layer.self_attn, dataset[0][None, :])[0]
    df_atten = pd.DataFrame([[entities[h], relations[r], entities[t]]+[features[j, i].item() for j in range(len(features))] for i, (h, r, t) in enumerate(input_)])
    df_atten.columns=['head', 'relation', 'tail',] + [f'atten_from{i}' for i in range(len(df_atten.columns)-3)]
    display(df_atten)
    # ヒートマップの作成
    # sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
    for i in range(len(df_atten)):
        display(i, df_atten.iloc[i,:3].tolist())
        display(df_atten.sort_values(f'atten_from{i}', ascending=False).iloc[:10,:3])
        print("----------")
    plt.show()
# heatmap_(300)

In [10]:
def make_heatmap2_(input_):
    assert len(input_) == 1
    features = extract(model, encoder_last_layer.self_attn, input_)[0]
    df_atten = pd.DataFrame([[entities[h], relations[r], entities[t]]+[features[j, i].item() for j in range(len(features))] for i, (h, r, t) in enumerate(input_[0])])
    df_atten.columns=['head', 'relation', 'tail',] + [f'atten_from{i}' for i in range(len(df_atten.columns)-3)]
    return df_atten

In [11]:
story_entities = triple_df['head'].tolist()
display(story_entities)

['<bos_e>',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 'AbbeyGrange:001',
 '<bos_e>',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 'AbbeyGrange:002',
 '<bos_e>',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 'AbbeyGrange:003',
 '<bos_e>',
 'AbbeyGrange:004',
 'AbbeyGrange:004',
 'AbbeyGrange:004',
 '<bos_e>',
 'AbbeyGrange:005',
 'AbbeyGrange:005',
 'AbbeyGrange:005',
 'AbbeyGrange:005',
 '<bos_e>',
 'AbbeyGrange:006',
 'AbbeyGrange:006',
 '<bos_e>',
 'AbbeyGrange:007',
 'AbbeyGrange:007',
 'AbbeyGrange:007',
 'AbbeyGrange:007',
 '<bos_e>',
 'AbbeyGrange:008',
 'AbbeyGrange:008',
 'AbbeyGrange:008',
 'AbbeyGrange:008',
 'AbbeyGrange:008',
 '<bos_e>',
 '<bos_e>',
 'AbbeyGrange:009a',
 'AbbeyGrange:009a',
 'AbbeyGrange:009a',
 'AbbeyGrange:009a',
 'AbbeyGrange:009a',
 '<bos_e>',
 'AbbeyGrange:009b',
 '

In [12]:
def make_ranking(_from, _to, _predicate, _whom, _subject, _why, _what, _where):
    if not (_from is None and _to is None):
        _start_index = story_entities.index(_from)-1 
        _end_index = len(story_entities) - story_entities[::-1].index(_to)
    else: 
        _start_index = 0
        _end_index = 0
    question_ = torch.tensor(
        [
            [d_e['<bos_e>'],d_r['<bos_r>'],d_e['<bos_e>']],
            [d_e['<mask_e>'],d_r['kgc:hasPredicate'],d_e[_predicate]],
            [d_e['<mask_e>'],d_r['kgc:whom'],d_e[_whom]],
            [d_e['<mask_e>'],d_r['kgc:subject'],d_e[_subject]],
            [d_e['<mask_e>'],d_r['kgc:why'],d_e[_why]],
            [d_e['<mask_e>'],d_r['kgc:what'],d_e[_what]],
            [d_e['<mask_e>'],d_r['kgc:where'],d_e[_where]],
        ]
    )
    mask_ = torch.tensor(
        [
            [False, False, False],
            [True, False, True],
            [True, False, True],
            [True, False, True],
            [True, False, True],
            [True, False, True],
            [True, False, True],
        ]
    )
    questions = torch.cat([triple[_start_index: _end_index], question_], dim=0).unsqueeze(0)
    masks = torch.cat([torch.zeros(_end_index-_start_index,3), mask_], dim=0).to(torch.bool).transpose(1,0).unsqueeze(0)
    tmp = []
    with torch.no_grad():
        _, (story_pred, relation_pred, entity_pred) = model(questions, masks[:,0], masks[:,1], masks[:,2])
        sorted_ = torch.argsort(entity_pred.to('cpu'), dim=1, descending=True)
        for i in range(sorted_.shape[1]):
            ans_= sorted_[:, i]
            predicate_, whom_, subj_, why_, what_, where_ = ans_
            tmp.append([entities[predicate_], entities[whom_], entities[subj_], entities[why_], entities[what_], entities[where_]])
    df_ranking = pd.DataFrame(tmp, columns=['predicate', 'whom', 'subject', 'why', 'what', 'where'])
    df_attension = make_heatmap2_(questions)
    return df_ranking, df_attension

In [13]:
MASK_E = '<mask_e>'
KILL = 'word.predicate:kill'
TAKE = 'word.predicate:take'
BRING = 'word.predicate:bring'
DIE = 'word.predicate:die'
HIDE = 'word.predicate:hide'

### まだらの紐
Who killed Julia? (criminal & explanation)
被害者: Julia
犯人: Roylott
犯行に用いたもの: snake
犯行動機: 母の相続財産を独占したい

In [15]:
victim = 'SpeckledBand:Julia'
killer = 'SpeckledBand:Roylott'
df_ranking_SpeckledBand, df_attension_SpeckledBand = make_ranking(
    'SpeckledBand:240', 'SpeckledBand:300', KILL, victim, MASK_E, MASK_E, MASK_E, MASK_E)

print(f"{killer}, ranking", df_ranking_SpeckledBand.index[df_ranking_SpeckledBand['subject']==killer].tolist())
display(df_ranking_SpeckledBand.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_SpeckledBand)
for i in range(len_):
    display(i, df_attension_SpeckledBand.iloc[i,:3].tolist())
    display(df_attension_SpeckledBand.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

SpeckledBand:Roylott, ranking [7]


predicate                               whom  \
0             word.predicate:exist     SpeckledBand:Roylott_s_bedroom   
1                  AllTitle:Watson       DateTime:1883-04-01T15:00:00   
2           word.predicate:examine                    AllTitle:Watson   
3              word.predicate:have                            <bos_e>   
4                          <bos_e>                    AllTitle:Holmes   
5     SpeckledBand:VentilationHole       SpeckledBand:Julia_s_bedroom   
6              word.predicate:pull       SpeckledBand:VentilationHole   
7     SpeckledBand:Julia_s_bedroom                 SpeckledBand:Helen   
8           word.predicate:notMove       DateTime:1883-04-01T16:00:00   
9     DateTime:1883-04-01T15:00:00               SpeckledBand:Roylott   
10  word.predicate:cannotGoThrough             ACaseOfIdentity:Hosmer   
11                 AllTitle:Holmes                  SpeckledBand:safe   
12               word.predicate:go                 SpeckledBand:Julia   
13  SpeckledBand:Roylott_s_bedroom          ACaseOfIdentity:Windibank   
14             word.predicate:make                  SpeckledBand:hole   
15              word.predicate:sit                   SpeckledBand:man   
16      SpeckledBand:1883-04-01T15            SpeckledBand:small_dish   
17          word.predicate:turnOff       DateTime:1881-04-01T10:00:00   
18    DateTime:1881-04-01T10:00:00  SpeckledBand:pull_of_the_doorbell   
19            word.predicate:smell       DateTime:1883-04-01T17:00:00   

                              subject  \
0      SpeckledBand:Roylott_s_bedroom   
1        SpeckledBand:Julia_s_bedroom   
2                     AllTitle:Holmes   
3        SpeckledBand:VentilationHole   
4                     AllTitle:Watson   
5                  SpeckledBand:Helen   
6                   SpeckledBand:hole   
7                SpeckledBand:Roylott   
8                    SpeckledBand:man   
9   SpeckledBand:pull_of_the_doorbell   
10                  SpeckledBand:safe   
11                 SpeckledBand:Julia   
12        SpeckledBand:Sleeping_Woman   
13                   SpeckledBand:bed   
14              SpeckledBand:dog_whip   
15          SpeckledBand:rope_of_bell   
16       DateTime:1883-04-01T15:00:00   
17            SpeckledBand:small_dish   
18    SpeckledBand:mansion_of_Roylott   
19               SpeckledBand:leopard   

                                                  why  \
0                                SpeckledBand:quietly   
1   SpeckledBand:Julia_suffered_from_the_smell_of_...   
2                                   SpeckledBand:safe   
3                          SpeckledBand:1883-04-01T17   
4                           SpeckledBand:simple_chair   
5                          SpeckledBand:corner_of_bed   
6                           SpeckledBand:intense_fear   
7                               SpeckledBand:headache   
8                                    SpeckledBand:130   
9                          SpeckledBand:1883-04-01T16   
10                               SpeckledBand:whistle   
11                            SpeckledBand:1883-05-01   
12                               SpeckledBand:tonight   
13                            SpeckledBand:OutsideAir   
14                           SpeckledBand:elbow_chair   
15                                SpeckledBand:signal   
16                             SpeckledBand:fireplace   
17                     SpeckledBand:reward_of_request   
18  SpeckledBand:by_falling_price_of_agricultural_...   
19                        SpeckledBand:strange_points   

                                 what  \
0                   SpeckledBand:safe   
1             SpeckledBand:small_dish   
2           SpeckledBand:simple_chair   
3                    SpeckledBand:cat   
4   SpeckledBand:pull_of_the_doorbell   
5          SpeckledBand:1883-04-01T17   
6                   SpeckledBand:lamp   
7        SpeckledBand:VentilationHole   
8      SpeckledBand:Roylott_s_bedroom   
9                    

0

['<bos_e>', '<bos_r>', '<bos_e>']

head     relation                            tail  \
51   SpeckledBand:249  kgc:subject            SpeckledBand:leopard   
1    SpeckledBand:240  kgc:subject  SpeckledBand:Roylott_s_bedroom   
114  SpeckledBand:260  kgc:subject                SpeckledBand:man   
34            <bos_e>      <bos_r>                         <bos_e>   
45            <bos_e>      <bos_r>                         <bos_e>   
35   SpeckledBand:246  kgc:subject                SpeckledBand:cat   
5             <bos_e>      <bos_r>                         <bos_e>   
40            <bos_e>      <bos_r>                         <bos_e>   
18            <bos_e>      <bos_r>                         <bos_e>   
92            <bos_e>      <bos_r>                         <bos_e>   
29            <bos_e>      <bos_r>                         <bos_e>   
54            <bos_e>      <bos_r>                         <bos_e>   
86            <bos_e>      <bos_r>                         <bos_e>   
129  SpeckledBand:262  kgc:subject              SpeckledBand:Helen   
67            <bos_e>      <bos_r>                         <bos_e>   
41   SpeckledBand:247  kgc:subject            SpeckledBand:Leopard   
58            <bos_e>      <bos_r>                         <bos_e>   
77            <bos_e>      <bos_r>                         <bos_e>   
19   SpeckledBand:243  kgc:subject               SpeckledBand:safe   
13            <bos_e>      <bos_r>                         <bos_e>   

     atten_from0  
51      0.005466  
1       0.005297  
114     0.005231  
34      0.005077  
45      0.005064  
35      0.005012  
5       0.004999  
40      0.004973  
18      0.004970  
92      0.004959  
29      0.004922  
54      0.004902  
86      0.004868  
129     0.004848  
67      0.004830  
41      0.004818  
58      0.004784  
77      0.004765  
19      0.004749  
13      0.004739

...

----------


320

['<mask_e>', 'kgc:where', '<mask_e>']

head   relation                            tail  \
2    SpeckledBand:240   kgc:what               SpeckledBand:safe   
99   SpeckledBand:258   kgc:what                SpeckledBand:264   
170  SpeckledBand:271   kgc:what    SpeckledBand:VentilationHole   
98   SpeckledBand:258   kgc:what                SpeckledBand:263   
85   SpeckledBand:256   kgc:time    DateTime:1883-04-01T17:00:00   
187  SpeckledBand:275   kgc:what  SpeckledBand:Indian_cigarettes   
89   SpeckledBand:257   kgc:what               SpeckledBand:plan   
101  SpeckledBand:258   kgc:what                SpeckledBand:267   
100  SpeckledBand:258   kgc:what                SpeckledBand:266   
104  SpeckledBand:258   kgc:time    DateTime:1883-04-01T17:00:00   
95   SpeckledBand:258   kgc:what                SpeckledBand:259   
16   SpeckledBand:242   kgc:what               SpeckledBand:safe   
53   SpeckledBand:249   kgc:what                SpeckledBand:cat   
97   SpeckledBand:258   kgc:what                SpeckledBand:262   
91   SpeckledBand:257   kgc:time    DateTime:1883-04-01T17:00:00   
72   SpeckledBand:253   kgc:time    DateTime:1883-04-01T17:00:00   
260  SpeckledBand:291   kgc:what              SpeckledBand:quiet   
119  SpeckledBand:261   kgc:what               SpeckledBand:261a   
123  SpeckledBand:261   kgc:time    DateTime:1883-04-01T21:00:00   
237  SpeckledBand:286  kgc:where    SpeckledBand:Julia_s_bedroom   

     atten_from320  
2         0.010909  
99        0.009914  
170       0.009871  
98        0.009770  
85        0.009745  
187       0.009372  
89        0.008989  
101       0.008909  
100       0.008464  
104       0.008186  
95        0.007685  
16        0.007663  
53        0.007619  
97        0.007567  
91        0.007466  
72        0.007118  
260       0.007037  
119       0.006907  
123       0.006755  
237       0.006635

----------


In [ ]:
victim = 'SpeckledBand:Julia'
df_ranking_SpeckledBand, df_attension_SpeckledBand = make_ranking(
    'SpeckledBand:330', 'SpeckledBand:400', KILL, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_SpeckledBand.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_SpeckledBand)
for i in range(len_-20, len_):
    display(i, df_attension_SpeckledBand.iloc[i,:3].tolist())
    display(df_attension_SpeckledBand.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                                  whom  \
0   word.predicate:cannotFind                    SpeckledBand:snake   
1         word.predicate:kill                       AllTitle:Holmes   
2       word.predicate:return                  SpeckledBand:Roylott   
3         word.predicate:bite                    SpeckledBand:Helen   
4          word.predicate:hit                       AllTitle:Watson   
5         word.predicate:hear                  word.predicate:angry   
6       word.predicate:goDown          DateTime:1883-04-01T23:00:00   
7        word.predicate:reach                 word.predicate:return   
8      word.predicate:putInto          SpeckledBand:VentilationHole   
9           word.predicate:go                               <bos_e>   
10     word.predicate:takeOut           SpeckledBand:sound_of_snake   
11     word.predicate:suspect  AbbeyGrange:Sir_Eustace_Brackenstall   
12        word.predicate:goUp            SpeckledBand:1883-04-01T23   
13   word.predicate:notNotice          SpeckledBand:Julia_s_bedroom   
14        word.predicate:give                word.predicate:putInto   
15   word.predicate:readAloud                  SpeckledBand:coroner   
16  word.predicate:notContact                    SpeckledBand:Julia   
17    word.predicate:callBack               SpeckledBand:ventilator   
18     word.predicate:pullOut          SpeckledBand:poison_of_snake   
19      word.predicate:wakeUp                     word.predicate:go   

                         subject                               why  \
0             SpeckledBand:snake        SpeckledBand:1883-04-01T23   
1                AllTitle:Holmes                SpeckledBand:snake   
2           SpeckledBand:Roylott       SpeckledBand:sound_of_snake   
3             SpeckledBand:Helen      DateTime:1883-04-01T23:00:00   
4              SpeckledBand:Safe               word.predicate:bite   
5              SpeckledBand:whip      SpeckledBand:VentilationHole   
6    SpeckledBand:sound_of_snake              word.predicate:angry   
7     SpeckledBand:1883-04-01T23             word.predicate:return   
8              SpeckledBand:safe                           <bos_e>   
9              SpeckledBand:milk                   AllTitle:Holmes   
10   SpeckledBand:metallic_sound                  SpeckledBand:069   
11             SpeckledBand:Roma  SilverBlaze:Insufficient_reasons   
12                       <bos_e>               word.predicate:hear   
13  DateTime:1883-04-01T23:00:00                   AbbeyGrange:023   
14  SpeckledBand:VentilationHole       SpeckledBand:metallic_sound   
15               AllTitle:Watson    SpeckledBand:reward_of_request   
16          word.predicate:angry                   SilverBlaze:363   
17           word.predicate:bite                 word.predicate:go   
18         SpeckledBand:dog_whip                 SpeckledBand:milk   
19  SpeckledBand:poison_of_snake      SpeckledBand:animal_of_India   

                            what                            where  
0             SpeckledBand:snake                SpeckledBand:safe  
1    SpeckledBand:sound_of_snake                AbbeyGrange:train  
2    SpeckledBand:metallic_sound               SpeckledBand:snake  
3           SpeckledBand:Roylott   SpeckledBand:Roylott_s_bedroom  
4                AllTitle:Holmes  SpeckledBand:mansion_of_Roylott  
5             AbbeyGrange:letter         AbbeyGrange:Abbey_Grange  
6              SpeckledBand:safe             SpeckledBand:Roylott  
7             SpeckledBand:Helen      SpeckledBand:sound_of_snake  
8                        <bos_e>               SpeckledBand:India  
9                AbbeyGrange:006       SpeckledBand:1883-04-01T23  
10    SpeckledBand:1883-04-01T23          AbbeyGrange:dining_room  
11             SpeckledBand:milk     DateTime:1883-04-01T23:00:00  
12  SpeckledBand:VentilationHole     SpeckledBand:VentilationHole  
13          word.predicate:angry     SpeckledBand:Julia_s_bedroom  
14               AbbeyGrange:004     

381

['SpeckledBand:398', 'kgc:time', 'DateTime:1883-04-01T23:00:00']

head          relation                          tail  \
375  SpeckledBand:397          kgc:time  DateTime:1883-04-01T23:00:00   
390  SpeckledBand:400  kgc:hasPredicate           word.predicate:bite   
381  SpeckledBand:398          kgc:time  DateTime:1883-04-01T23:00:00   
364  SpeckledBand:395          kgc:time  DateTime:1883-04-01T23:00:00   
391  SpeckledBand:400          kgc:what          SpeckledBand:Roylott   
393  SpeckledBand:400          kgc:time  DateTime:1883-04-01T23:00:00   
370  SpeckledBand:396          kgc:time  DateTime:1883-04-01T23:00:00   
378  SpeckledBand:398  kgc:hasPredicate         word.predicate:return   
379  SpeckledBand:398            kgc:to  SpeckledBand:VentilationHole   
392  SpeckledBand:400          kgc:when    SpeckledBand:1883-04-01T23   
388           <bos_e>           <bos_r>                       <bos_e>   
384  SpeckledBand:399  kgc:hasPredicate         word.predicate:return   
394           <bos_e>           <bos_r>                       <bos_e>   
380  SpeckledBand:398          kgc:when    SpeckledBand:1883-04-01T23   
385  SpeckledBand:399            kgc:to          SpeckledBand:Roylott   
374  SpeckledBand:397          kgc:when    SpeckledBand:1883-04-01T23   
387  SpeckledBand:399          kgc:time  DateTime:1883-04-01T23:00:00   
376           <bos_e>           <bos_r>                       <bos_e>   
382           <bos_e>           <bos_r>                       <bos_e>   
371           <bos_e>           <bos_r>                       <bos_e>   

     atten_from381  
375       0.042594  
390       0.033843  
381       0.030526  
364       0.028682  
391       0.026474  
393       0.023171  
370       0.022709  
378       0.021576  
379       0.021039  
392       0.021015  
388       0.019737  
384       0.019663  
394       0.019187  
380       0.018775  
385       0.018666  
374       0.018648  
387       0.018030  
376       0.017561  
382       0.017506  
371       0.017375

----------


...

----------


400

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation                          tail  \
393  SpeckledBand:400          kgc:time  DateTime:1883-04-01T23:00:00   
381  SpeckledBand:398          kgc:time  DateTime:1883-04-01T23:00:00   
375  SpeckledBand:397          kgc:time  DateTime:1883-04-01T23:00:00   
390  SpeckledBand:400  kgc:hasPredicate           word.predicate:bite   
387  SpeckledBand:399          kgc:time  DateTime:1883-04-01T23:00:00   
399          <mask_e>          kgc:what                      <mask_e>   
391  SpeckledBand:400          kgc:what          SpeckledBand:Roylott   
364  SpeckledBand:395          kgc:time  DateTime:1883-04-01T23:00:00   
392  SpeckledBand:400          kgc:when    SpeckledBand:1883-04-01T23   
370  SpeckledBand:396          kgc:time  DateTime:1883-04-01T23:00:00   
395          <mask_e>  kgc:hasPredicate           word.predicate:kill   
396          <mask_e>          kgc:whom            SpeckledBand:Julia   
384  SpeckledBand:399  kgc:hasPredicate         word.predicate:return   
389  SpeckledBand:400       kgc:subject            SpeckledBand:snake   
372  SpeckledBand:397       kgc:subject            SpeckledBand:snake   
398          <mask_e>           kgc:why                      <mask_e>   
386  SpeckledBand:399          kgc:when    SpeckledBand:1883-04-01T23   
383  SpeckledBand:399       kgc:subject            SpeckledBand:snake   
368  SpeckledBand:396          kgc:what            SpeckledBand:snake   
397          <mask_e>       kgc:subject                      <mask_e>   

     atten_from400  
393       0.062672  
381       0.058865  
375       0.045056  
390       0.042465  
387       0.039452  
399       0.037132  
391       0.030713  
364       0.027462  
392       0.026382  
370       0.025910  
395       0.024853  
396       0.023789  
384       0.020180  
389       0.019182  
372       0.018218  
398       0.016888  
386       0.016493  
383       0.016261  
368       0.015994  
397       0.014984

----------


### 悪魔の足跡１
Who killed the victims? (criminal & explanation)
被害者: Brenda
犯人: Mortimer
犯行動機: 財産

In [ ]:
victim = 'DevilsFoot:Brenda'
killer = 'DevilsFoot:Mortimer'
df_ranking_DevilsFoot1, df_attension_DevilsFoot1 = make_ranking(
    None, None, KILL, victim, MASK_E, MASK_E, MASK_E, MASK_E)

print(f"{killer}, ranking", df_ranking_DevilsFoot1.index[df_ranking_DevilsFoot1['subject'] == killer].tolist()[0])
display(df_ranking_DevilsFoot1.iloc[:20,:])

# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_DevilsFoot1)
for i in range(len_):
    display(i, df_attension_DevilsFoot1.iloc[i,:3].tolist())
    display(df_attension_DevilsFoot1.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

DevilsFoot:Mortimer, ranking 50


predicate                                       whom  \
0      word.predicate:testify                        word.predicate:hold   
1      word.predicate:notHave                   SilverBlaze:John_Straker   
2      word.predicate:suspect                      word.predicate:become   
3         word.predicate:hold                          DevilsFoot:Brenda   
4      word.predicate:contain          SilverBlaze:Night_of_the_incident   
5       word.predicate:wander                        word.predicate:meet   
6    word.predicate:self-harm                      word.predicate:manage   
7         word.predicate:kill               SilverBlaze:1896-04-02T00:00   
8        word.predicate:avoid                   SilverBlaze:Silver_Blaze   
9       word.predicate:become                SilverBlaze:Fitzroy_Simpson   
10       word.predicate:fight                                    <bos_e>   
11       word.predicate:bring                         word.predicate:say   
12    word.predicate:handOver                          word.predicate:go   
13         word.predicate:bet                       word.predicate:fight   
14  word.predicate:notInjured  SilverBlaze:Disappearance_of_Silver_Blaze   
15      word.predicate:excuse                   word.predicate:self-harm   
16       word.predicate:train                     word.predicate:suspect   
17         word.predicate:say                     ACaseOfIdentity:Hosmer   
18      word.predicate:manage                       word.predicate:sleep   
19     word.predicate:collect                        word.predicate:show   

                                      subject  \
0                 SilverBlaze:Fitzroy_Simpson   
1                    SilverBlaze:John_Straker   
2                    SilverBlaze:Silver_Blaze   
3               SilverBlaze:Inspector_Gregory   
4                           SilverBlaze:knife   
5                SilverBlaze:A_group_of_Gypsy   
6          SilverBlaze:Corpse_of_John_Straker   
7                      SilverBlaze:wilderness   
8            SilverBlaze:Wife_of_John_Straker   
9                           SilverBlaze:Horse   
10  SilverBlaze:Disappearance_of_Silver_Blaze   
11                          SilverBlaze:paper   
12                  SilverBlaze:two_young_men   
13          SilverBlaze:Night_of_the_incident   
14  SilverBlaze:Reasoning_Detective_of_police   
15   SilverBlaze:The_total_amount_of_the_bill   
16                           SilverBlaze:rain   
17                         SilverBlaze:police   
18       SilverBlaze:Curry_dish_of_Ned_Hunter   
19                      ACaseOfIdentity:Woman   

                                 why  \
0              SilverBlaze:In_combat   
1        SilverBlaze:Fitzroy_Simpson   
2                    SilverBlaze:192   
3                    SilverBlaze:191   
4                    SilverBlaze:188   
5           SilverBlaze:Silver_Blaze   
6                    SilverBlaze:190   
7   SilverBlaze:Head_of_John_Straker   
8                    SilverBlaze:189   
9                    SilverBlaze:273   
10                 SilverBlaze:knife   
11                   SilverBlaze:271   
12                   SilverBlaze:275   
13                   SilverBlaze:274   
14                 SilverBlaze:Horse   
15  SilverBlaze:Insufficient_reasons   
16                   SilverBlaze:276   
17                   SilverBlaze:241   
18                SilverBlaze:letter   
19                   SilverBlaze:272   

                                                 what  \
0                            SilverBlaze:Silver_Blaze   
1                    SilverBlaze:Head_of_John_Straker   
2                               SilverBlaze:In_combat   
3                                   SilverBlaze:knife   
4                         SilverBlaze:Fitzroy_Simpson   
5                                     SilverBlaze:186   
6                                  SilverBlaze:candle   
7                             SilverBlaze:Thick_stick   
8                                     S

0

['<bos_e>', '<bos_r>', '<bos_e>']

head          relation                 tail  atten_from0
0   <bos_e>           <bos_r>              <bos_e>     0.233659
5  <mask_e>          kgc:what             <mask_e>     0.170707
2  <mask_e>          kgc:whom    DevilsFoot:Brenda     0.163049
4  <mask_e>           kgc:why             <mask_e>     0.132533
6  <mask_e>         kgc:where             <mask_e>     0.117240
3  <mask_e>       kgc:subject             <mask_e>     0.101302
1  <mask_e>  kgc:hasPredicate  word.predicate:kill     0.081510

...

----------


6

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation                 tail  atten_from6
2  <mask_e>          kgc:whom    DevilsFoot:Brenda     0.289802
0   <bos_e>           <bos_r>              <bos_e>     0.266778
3  <mask_e>       kgc:subject             <mask_e>     0.110762
5  <mask_e>          kgc:what             <mask_e>     0.097785
6  <mask_e>         kgc:where             <mask_e>     0.092083
4  <mask_e>           kgc:why             <mask_e>     0.077956
1  <mask_e>  kgc:hasPredicate  word.predicate:kill     0.064834

----------


In [ ]:
victim = 'DevilsFoot:Brenda'
df_ranking_DevilsFoot1, df_attension_DevilsFoot1 = make_ranking(
    'DevilsFoot:420', 'DevilsFoot:488', KILL, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_DevilsFoot1.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_DevilsFoot1)
for i in range(len_-20, len_):
    display(i, df_attension_DevilsFoot1.iloc[i,:3].tolist())
    display(df_attension_DevilsFoot1.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                                             whom  \
0       word.predicate:kill                                DevilsFoot:Brenda   
1      word.predicate:check                             DevilsFoot:Sterndale   
2     word.predicate:wander                                  DevilsFoot:Owen   
3       word.predicate:fire                                  AllTitle:Holmes   
4      word.predicate:stand                              DevilsFoot:Mortimer   
5        word.predicate:die                                DevilsFoot:George   
6        word.predicate:put                               DevilsFoot:Brother   
7   word.predicate:notExist                                          <bos_e>   
8       word.predicate:show  DevilsFoot:Exclusive_manager_of_shared_property   
9     word.predicate:beUsed                              word.predicate:meet   
10    word.predicate:become                                  DevilsFoot:lawn   
11   word.predicate:notHave                       DevilsFoot:Powder_medicine   
12     word.predicate:enter                                 CrookedMan:Nancy   
13      word.predicate:come                DevilsFoot:Another_interpretation   
14     word.predicate:shoot                              DevilsFoot:neighbor   
15     word.predicate:think                                 DevilsFoot:truth   
16   word.predicate:contain                                  DevilsFoot:Drug   
17   word.predicate:suspect                              word.predicate:kill   
18      word.predicate:meet                                 DevilsFoot:Chair   
19      word.predicate:live                             AbbeyGrange:Criminal   

                                       subject  \
0                         DevilsFoot:Sterndale   
1                          DevilsFoot:Mortimer   
2                   DevilsFoot:Powder_medicine   
3                         AbbeyGrange:Criminal   
4                              AllTitle:Holmes   
5            DevilsFoot:Another_interpretation   
6                DevilsFoot:European_chemistry   
7                      word.predicate:notExist   
8                                      <bos_e>   
9                            DevilsFoot:gravel   
10                             DevilsFoot:Owen   
11                       DevilsFoot:Magic_foot   
12             DevilsFoot:sample_of_magic_foot   
13                           DevilsFoot:George   
14                             DevilsFoot:Drug   
15                          DevilsFoot:Failure   
16  DevilsFoot:Starting_point_of_investigation   
17       DevilsFoot:Mortimer_sImmediate_family   
18                            DevilsFoot:truth   
19             ResidentPatient:Percy_Trevelyan   

                                     why  \
0                       DevilsFoot:money   
1             DevilsFoot:Powder_medicine   
2      DevilsFoot:Another_interpretation   
3                        AbbeyGrange:221   
4      DevilsFoot:laws_of_United_Kingdom   
5          DevilsFoot:Five_minutes_later   
6                   DevilsFoot:Sterndale   
7                      DevilsFoot:gravel   
8                        AbbeyGrange:219   
9                        AbbeyGrange:200   
10  SilverBlaze:State_of_Fitzroy_Simpson   
11                       DevilsFoot:fear   
12                       SilverBlaze:271   
13                      DevilsFoot:Chair   
14          DevilsFoot:control_of_George   
15                               <bos_e>   
16                       DevilsFoot:room   
17      DevilsFoot:rare_object_of_Africa   
18                 word.predicate:gravel   
19                 DevilsFoot:Magic_foot   

                                    what  \
0             DevilsFoot:Powder_medicine   
1                         DevilsFoot:gun   
2      DevilsFoot:Another_interpretation   
3                   DevilsFoot:Sterndale   
4                        DevilsFoot:fire   
5                 DevilsFoot:Information   
6                         DevilsFoot:460   
7        

304

['DevilsFoot:485', 'kgc:what', 'DevilsFoot:gun']

head          relation                          tail  \
319        <mask_e>          kgc:whom             DevilsFoot:Brenda   
304  DevilsFoot:485          kgc:what                DevilsFoot:gun   
303  DevilsFoot:485  kgc:hasPredicate           word.predicate:hold   
318        <mask_e>  kgc:hasPredicate           word.predicate:kill   
256  DevilsFoot:473          kgc:what                DevilsFoot:483   
282  DevilsFoot:480  kgc:hasPredicate          word.predicate:shoot   
252  DevilsFoot:473          kgc:what                DevilsFoot:479   
322        <mask_e>          kgc:what                      <mask_e>   
257  DevilsFoot:473          kgc:what                DevilsFoot:484   
258  DevilsFoot:473          kgc:what                DevilsFoot:485   
254  DevilsFoot:473          kgc:what                DevilsFoot:481   
253  DevilsFoot:473          kgc:what                DevilsFoot:480   
259  DevilsFoot:473          kgc:what                DevilsFoot:486   
300  DevilsFoot:484         kgc:where  DevilsFoot:Outside_of_window   
250  DevilsFoot:473          kgc:what                DevilsFoot:477   
249  DevilsFoot:473          kgc:what                DevilsFoot:476   
247  DevilsFoot:473          kgc:what                DevilsFoot:474   
285  DevilsFoot:481       kgc:subject           DevilsFoot:Mortimer   
248  DevilsFoot:473          kgc:what                DevilsFoot:475   
283  DevilsFoot:480          kgc:what           DevilsFoot:Mortimer   

     atten_from304  
319       0.047456  
304       0.047002  
303       0.034903  
318       0.027333  
256       0.023130  
282       0.021358  
252       0.020132  
322       0.019683  
257       0.019628  
258       0.018274  
254       0.017288  
253       0.016849  
259       0.016492  
300       0.016288  
250       0.015927  
249       0.015765  
247       0.015405  
285       0.014946  
248       0.014420  
283       0.013723

----------


...

----------


323

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation  \
319        <mask_e>          kgc:whom   
310  DevilsFoot:487       kgc:subject   
322        <mask_e>          kgc:what   
316  DevilsFoot:488         kgc:where   
318        <mask_e>  kgc:hasPredicate   
323        <mask_e>         kgc:where   
306  DevilsFoot:486       kgc:subject   
320        <mask_e>       kgc:subject   
254  DevilsFoot:473          kgc:what   
314  DevilsFoot:488       kgc:subject   
321        <mask_e>           kgc:why   
259  DevilsFoot:473          kgc:what   
250  DevilsFoot:473          kgc:what   
256  DevilsFoot:473          kgc:what   
249  DevilsFoot:473          kgc:what   
300  DevilsFoot:484         kgc:where   
302  DevilsFoot:485       kgc:subject   
257  DevilsFoot:473          kgc:what   
247  DevilsFoot:473          kgc:what   
294  DevilsFoot:483       kgc:subject   

                                           tail  atten_from323  
319                           DevilsFoot:Brenda       0.112661  
310  DevilsFoot:Starting_point_of_investigation       0.044756  
322                                    <mask_e>       0.035589  
316          DevilsFoot:garden_of_pastoral_hall       0.030131  
318                         word.predicate:kill       0.027820  
323                                    <mask_e>       0.027743  
306                         DevilsFoot:Mortimer       0.026872  
320                                    <mask_e>       0.026284  
254                              DevilsFoot:481       0.025006  
314                           DevilsFoot:gravel       0.022644  
321                                    <mask_e>       0.020035  
259                              DevilsFoot:486       0.019627  
250                              DevilsFoot:477       0.018972  
256                              DevilsFoot:483       0.018485  
249                              DevilsFoot:476       0.018430  
300                DevilsFoot:Outside_of_window       0.017962  
302                        DevilsFoot:Sterndale       0.017759  
257                              DevilsFoot:484       0.017693  
247                              DevilsFoot:474       0.016072  
294                        DevilsFoot:Sterndale       0.015804

----------


### 悪魔の足跡2
Who killed the victims? (criminal & explanation)
被害者: Mortimer
犯人: 
犯行動機: 恋人の敵

In [ ]:
victim = 'DevilsFoot:Mortimer'
killer = 'DevilsFoot:Sterndale'
df_ranking_DevilsFoot1, df_attension_DevilsFoot1 = make_ranking(
    None, None, KILL, victim, MASK_E, MASK_E, MASK_E, MASK_E)

print(f"{killer}, ranking", df_ranking_DevilsFoot1.index[df_ranking_DevilsFoot1['subject'] == killer].tolist()[0])
display(df_ranking_DevilsFoot1.iloc[:20,:])

# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_DevilsFoot1)
for i in range(len_):
    display(i, df_attension_DevilsFoot1.iloc[i,:3].tolist())
    display(df_attension_DevilsFoot1.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

DevilsFoot:Sterndale, ranking 7


predicate                       whom  \
0        word.predicate:wander        word.predicate:hold   
1          word.predicate:hold         word.predicate:say   
2       word.predicate:notHave          word.predicate:go   
3       word.predicate:suspect       word.predicate:think   
4       word.predicate:testify        word.predicate:meet   
5          word.predicate:kill      word.predicate:become   
6            word.predicate:go    word.predicate:handOver   
7      word.predicate:handOver                    <bos_e>   
8           word.predicate:say        DevilsFoot:Mortimer   
9        word.predicate:become        word.predicate:find   
10        word.predicate:avoid        word.predicate:want   
11         word.predicate:move     word.predicate:consult   
12  word.predicate:leaveBehind      word.predicate:wander   
13      word.predicate:contain         word.predicate:ask   
14         word.predicate:find        word.predicate:wear   
15        word.predicate:worry        word.predicate:know   
16         word.predicate:feel        word.predicate:move   
17       word.predicate:search  word.predicate:profitable   
18      word.predicate:notSeem        word.predicate:have   
19        word.predicate:think        word.predicate:open   

                                     subject                     why  \
0                      word.predicate:wander        DevilsFoot:money   
1                          SilverBlaze:knife   word.predicate:wander   
2                            AllTitle:Holmes         SilverBlaze:272   
3                                    <bos_e>                 <bos_e>   
4                            AllTitle:Watson         SilverBlaze:278   
5                         word.predicate:say         SilverBlaze:191   
6                          SilverBlaze:paper         SilverBlaze:273   
7                       DevilsFoot:Sterndale         SilverBlaze:270   
8                        DevilsFoot:Mortimer         SilverBlaze:271   
9              SilverBlaze:Inspector_Gregory  word.predicate:consult   
10                       word.predicate:hold         SilverBlaze:192   
11                          SilverBlaze:rain         SilverBlaze:275   
12           ResidentPatient:Percy_Trevelyan       SilverBlaze:knife   
13                     ACaseOfIdentity:Woman   SilverBlaze:In_combat   
14               ResidentPatient:Elderly_man      word.predicate:say   
15                  SilverBlaze:Silver_Blaze         SilverBlaze:276   
16                           DevilsFoot:Drug         SilverBlaze:274   
17        SilverBlaze:Corpse_of_John_Straker     word.predicate:hold   
18  SilverBlaze:The_total_amount_of_the_bill        SilverBlaze:rain   
19                       word.predicate:want         SilverBlaze:188   

                                                 what  \
0                                   SilverBlaze:knife   
1                                 word.predicate:hold   
2                                             <bos_e>   
3                                  word.predicate:say   
4                               word.predicate:wander   
5                                   SilverBlaze:paper   
6   SilverBlaze:Letter_of_instructions_from_Colone...   
7   SilverBlaze:Three_pieces_of_receipt_already_in...   
8                   SilverBlaze:Place_of_Silver_Blaze   
9                            SilverBlaze:Silver_Blaze   
10                                    SilverBlaze:186   
11                                  word.predicate:go   
12                                     DevilsFoot:air   
13                             word.predicate:receive   
14                                  DevilsFoot:gravel   
15                            SilverBlaze:Thick_stick   
16                              SilverBlaze:Wax_match   
17                                word.predicate:want   
18                                 SilverBlaze:candle   
19                         SilverBlaze:expensive_wear   

                            

0

['<bos_e>', '<bos_r>', '<bos_e>']

head          relation                 tail  atten_from0
2  <mask_e>          kgc:whom  DevilsFoot:Mortimer     0.184417
5  <mask_e>          kgc:what             <mask_e>     0.171995
0   <bos_e>           <bos_r>              <bos_e>     0.163528
6  <mask_e>         kgc:where             <mask_e>     0.144002
4  <mask_e>           kgc:why             <mask_e>     0.130367
3  <mask_e>       kgc:subject             <mask_e>     0.104645
1  <mask_e>  kgc:hasPredicate  word.predicate:kill     0.101045

...

----------


6

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation                 tail  atten_from6
2  <mask_e>          kgc:whom  DevilsFoot:Mortimer     0.322025
0   <bos_e>           <bos_r>              <bos_e>     0.203524
6  <mask_e>         kgc:where             <mask_e>     0.114817
5  <mask_e>          kgc:what             <mask_e>     0.113813
3  <mask_e>       kgc:subject             <mask_e>     0.093295
4  <mask_e>           kgc:why             <mask_e>     0.084803
1  <mask_e>  kgc:hasPredicate  word.predicate:kill     0.067722

----------


In [ ]:
victim = 'DevilsFoot:Mortimer'
df_ranking_DevilsFoot2, df_attension_DevilsFoot2 = make_ranking(
    'DevilsFoot:420', 'DevilsFoot:488', KILL, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_DevilsFoot2.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_DevilsFoot2)
for i in range(len_-20, len_):
    display(i, df_attension_DevilsFoot2.iloc[i,:3].tolist())
    display(df_attension_DevilsFoot2.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                                             whom  \
0       word.predicate:kill                              DevilsFoot:Mortimer   
1      word.predicate:check                             DevilsFoot:Sterndale   
2     word.predicate:wander                                  AllTitle:Holmes   
3      word.predicate:stand                                  DevilsFoot:Owen   
4       word.predicate:fire                                DevilsFoot:George   
5        word.predicate:die                               DevilsFoot:Brother   
6        word.predicate:put  DevilsFoot:Exclusive_manager_of_shared_property   
7      word.predicate:enter                                DevilsFoot:Brenda   
8     word.predicate:become                              word.predicate:meet   
9     word.predicate:beUsed                              DevilsFoot:neighbor   
10      word.predicate:show                                          <bos_e>   
11  word.predicate:notExist                              DevilsFoot:Criminal   
12     word.predicate:think                       DevilsFoot:Powder_medicine   
13     word.predicate:shoot                               word.predicate:say   
14      word.predicate:come                             word.predicate:think   
15   word.predicate:contain                              word.predicate:kill   
16    word.predicate:direct                                 DevilsFoot:truth   
17  word.predicate:blowAway                            word.predicate:become   
18       word.predicate:act                             word.predicate:enter   
19     word.predicate:leave                           DevilsFoot:Living_room   

                                       subject  \
0                         DevilsFoot:Sterndale   
1                          DevilsFoot:Mortimer   
2                   DevilsFoot:Powder_medicine   
3                              AllTitle:Holmes   
4                         AbbeyGrange:Criminal   
5            DevilsFoot:Another_interpretation   
6                DevilsFoot:European_chemistry   
7                                      <bos_e>   
8                        DevilsFoot:Magic_foot   
9                      word.predicate:notExist   
10                           DevilsFoot:gravel   
11                             DevilsFoot:Owen   
12                           DevilsFoot:George   
13       DevilsFoot:Mortimer_sImmediate_family   
14  DevilsFoot:Starting_point_of_investigation   
15                          DevilsFoot:Failure   
16                             DevilsFoot:Drug   
17             DevilsFoot:sample_of_magic_foot   
18                            DevilsFoot:truth   
19                       word.predicate:wander   

                                     why  \
0                       DevilsFoot:money   
1             DevilsFoot:Powder_medicine   
2      DevilsFoot:Another_interpretation   
3                        AbbeyGrange:221   
4      DevilsFoot:laws_of_United_Kingdom   
5          DevilsFoot:Five_minutes_later   
6                   DevilsFoot:Sterndale   
7                      DevilsFoot:gravel   
8                  DevilsFoot:Magic_foot   
9                       DevilsFoot:Chair   
10                       DevilsFoot:fear   
11                       AbbeyGrange:200   
12             DevilsFoot:Attack_of_fear   
13                        DevilsFoot:449   
14          DevilsFoot:control_of_George   
15                   DevilsFoot:Mortimer   
16                        DevilsFoot:450   
17      DevilsFoot:rare_object_of_Africa   
18  SilverBlaze:State_of_Fitzroy_Simpson   
19                 word.predicate:gravel   

                                    what  \
0             DevilsFoot:Powder_medicine   
1                         DevilsFoot:gun   
2                 DevilsFoot:Information   
3      DevilsFoot:Another_interpretation   
4                   DevilsFoot:Sterndale   
5                        DevilsFoot:fire   
6                         DevilsFoot:453   
7        

304

['DevilsFoot:485', 'kgc:what', 'DevilsFoot:gun']

head          relation                          tail  \
319        <mask_e>          kgc:whom           DevilsFoot:Mortimer   
304  DevilsFoot:485          kgc:what                DevilsFoot:gun   
303  DevilsFoot:485  kgc:hasPredicate           word.predicate:hold   
318        <mask_e>  kgc:hasPredicate           word.predicate:kill   
256  DevilsFoot:473          kgc:what                DevilsFoot:483   
282  DevilsFoot:480  kgc:hasPredicate          word.predicate:shoot   
252  DevilsFoot:473          kgc:what                DevilsFoot:479   
257  DevilsFoot:473          kgc:what                DevilsFoot:484   
322        <mask_e>          kgc:what                      <mask_e>   
258  DevilsFoot:473          kgc:what                DevilsFoot:485   
254  DevilsFoot:473          kgc:what                DevilsFoot:481   
253  DevilsFoot:473          kgc:what                DevilsFoot:480   
259  DevilsFoot:473          kgc:what                DevilsFoot:486   
300  DevilsFoot:484         kgc:where  DevilsFoot:Outside_of_window   
250  DevilsFoot:473          kgc:what                DevilsFoot:477   
249  DevilsFoot:473          kgc:what                DevilsFoot:476   
247  DevilsFoot:473          kgc:what                DevilsFoot:474   
248  DevilsFoot:473          kgc:what                DevilsFoot:475   
285  DevilsFoot:481       kgc:subject           DevilsFoot:Mortimer   
255  DevilsFoot:473          kgc:what                DevilsFoot:482   

     atten_from304  
319       0.046982  
304       0.046647  
303       0.034422  
318       0.026584  
256       0.023880  
282       0.021326  
252       0.020250  
257       0.020152  
322       0.018822  
258       0.018718  
254       0.017497  
253       0.017224  
259       0.016791  
300       0.016491  
250       0.016332  
249       0.016235  
247       0.015790  
248       0.014649  
285       0.014118  
255       0.013776

----------


...

----------


323

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation  \
319        <mask_e>          kgc:whom   
310  DevilsFoot:487       kgc:subject   
322        <mask_e>          kgc:what   
316  DevilsFoot:488         kgc:where   
323        <mask_e>         kgc:where   
318        <mask_e>  kgc:hasPredicate   
320        <mask_e>       kgc:subject   
254  DevilsFoot:473          kgc:what   
306  DevilsFoot:486       kgc:subject   
314  DevilsFoot:488       kgc:subject   
321        <mask_e>           kgc:why   
250  DevilsFoot:473          kgc:what   
249  DevilsFoot:473          kgc:what   
256  DevilsFoot:473          kgc:what   
259  DevilsFoot:473          kgc:what   
300  DevilsFoot:484         kgc:where   
257  DevilsFoot:473          kgc:what   
247  DevilsFoot:473          kgc:what   
302  DevilsFoot:485       kgc:subject   
251  DevilsFoot:473          kgc:what   

                                           tail  atten_from323  
319                         DevilsFoot:Mortimer       0.127997  
310  DevilsFoot:Starting_point_of_investigation       0.043018  
322                                    <mask_e>       0.035138  
316          DevilsFoot:garden_of_pastoral_hall       0.030385  
323                                    <mask_e>       0.028289  
318                         word.predicate:kill       0.027090  
320                                    <mask_e>       0.025424  
254                              DevilsFoot:481       0.025274  
306                         DevilsFoot:Mortimer       0.023731  
314                           DevilsFoot:gravel       0.022561  
321                                    <mask_e>       0.020260  
250                              DevilsFoot:477       0.019386  
249                              DevilsFoot:476       0.019314  
256                              DevilsFoot:483       0.019264  
259                              DevilsFoot:486       0.019235  
300                DevilsFoot:Outside_of_window       0.018613  
257                              DevilsFoot:484       0.017709  
247                              DevilsFoot:474       0.016393  
302                        DevilsFoot:Sterndale       0.016351  
251                              DevilsFoot:478       0.015426

----------


### 背中の曲がった男: 
Why did Barclay die?
被害者: Barclay
犯人: 
犯行動機: 

In [ ]:
victim = 'CrookedMan:Barclay'
killer = 'CrookedMan:apoplexia'
df_ranking_CrookedMan, df_attension_CrookedMan = make_ranking(
    None, None, DIE, MASK_E, victim, MASK_E, MASK_E, MASK_E)

print(f"{killer}, ranking", df_ranking_CrookedMan.index[df_ranking_CrookedMan['why'] == killer].tolist()[0])
display(df_ranking_CrookedMan.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_CrookedMan)
for i in range(len_-20, len_):
    display(i, df_attension_CrookedMan.iloc[i,:3].tolist())
    display(df_attension_CrookedMan.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

CrookedMan:apoplexia, ranking 611


predicate                               whom  \
0       word.predicate:wander                   SilverBlaze:camp   
1           word.predicate:go           SilverBlaze:Silver_Blaze   
2        word.predicate:bring                            <bos_e>   
3        word.predicate:fight  SilverBlaze:Place_of_Silver_Blaze   
4      word.predicate:notHave                  word.predicate:go   
5         word.predicate:meet                    SilverBlaze:186   
6         word.predicate:have              SilverBlaze:In_combat   
7    word.predicate:self-harm                word.predicate:meet   
8         word.predicate:hide           word.predicate:self-harm   
9          word.predicate:say   SilverBlaze:Head_of_John_Straker   
10       word.predicate:visit               word.predicate:bring   
11        word.predicate:mash                  SilverBlaze:knife   
12  word.predicate:profitable        SilverBlaze:Fitzroy_Simpson   
13                    <bos_e>                 word.predicate:say   
14         word.predicate:die          SilverBlaze:King_s_Pyland   
15  word.predicate:notInjured                word.predicate:mash   
16        word.predicate:gain               word.predicate:fight   
17      word.predicate:attend             ACaseOfIdentity:Hosmer   
18       word.predicate:avoid              word.predicate:wander   
19      word.predicate:return               SilverBlaze:incident   

                                              subject  \
0                         SilverBlaze:Fitzroy_Simpson   
1                        SilverBlaze:A_group_of_Gypsy   
2                                             <bos_e>   
3                                  CrookedMan:Barclay   
4                                    SilverBlaze:rain   
5                            SilverBlaze:Silver_Blaze   
6                                    SilverBlaze:camp   
7                   SilverBlaze:Place_of_Silver_Blaze   
8                                   SilverBlaze:knife   
9   SilverBlaze:Depression_in_the_direction_of_Map...   
10                           SilverBlaze:John_Straker   
11                                    AllTitle:Watson   
12                              SilverBlaze:In_combat   
13                            AbbeyGrange:Jack_Croker   
14                                  SilverBlaze:Gypsy   
15                         ACaseOfIdentity:Sutherland   
16                      SilverBlaze:Inspector_Gregory   
17                   SilverBlaze:Head_of_John_Straker   
18                                    AllTitle:Holmes   
19                        ACaseOfIdentity:Dance_party   

                                 why  \
0              SilverBlaze:In_combat   
1                    SilverBlaze:192   
2                            <bos_e>   
3                    SilverBlaze:270   
4                    SilverBlaze:273   
5   SilverBlaze:Head_of_John_Straker   
6                    SilverBlaze:278   
7                    SilverBlaze:191   
8                    SilverBlaze:186   
9                    SilverBlaze:271   
10                   SilverBlaze:272   
11  SilverBlaze:Insufficient_reasons   
12                 SilverBlaze:knife   
13                   SilverBlaze:188   
14                   SilverBlaze:189   
15                   SilverBlaze:190   
16                   SilverBlaze:276   
17                  SilverBlaze:rain   
18                   SilverBlaze:275   
19          SilverBlaze:Silver_Blaze   

                                        what  \
0          SilverBlaze:Place_of_Silver_Blaze   
1           SilverBlaze:Head_of_John_Straker   
2                          SilverBlaze:knife   
3                                    <bos_e>   
4                           SilverBlaze:camp   
5                            SilverBlaze:186   
6                      SilverBlaze:In_combat   
7                    SilverBlaze:Thick_stick   
8                   SilverBlaze:Silver_Blaze   
9   SilverBlaze:Duplicate_key_of_the_stables   
10               SilverB

IndexError: single positional indexer is out-of-bounds

In [ ]:
victim = 'CrookedMan:Barclay'
df_ranking_CrookedMan, df_attension_CrookedMan = make_ranking(
    'CrookedMan:300', 'CrookedMan:372', DIE, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_CrookedMan.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_CrookedMan)
for i in range(len_-20, len_):
    display(i, df_attension_CrookedMan.iloc[i,:3].tolist())
    display(df_attension_CrookedMan.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                                       whom  \
0             word.predicate:die                            AllTitle:Holmes   
1            word.predicate:call                         CrookedMan:Barclay   
2             word.predicate:see              AbbeyGrange:Lady_Brackenstall   
3           word.predicate:exist                          CrookedMan:police   
4            word.predicate:pale                          CrookedMan:Davide   
5   word.predicate:notContradict                          CrookedMan:Murphy   
6            word.predicate:help       AbbeyGrange:Sir_Eustace_Brackenstall   
7          word.predicate:return                           CrookedMan:Nancy   
8            word.predicate:live                            AllTitle:Watson   
9          word.predicate:arrive  CrookedMan:episode_of_Uriah_and_Bathsheba   
10            word.predicate:say                           CrookedMan:Henry   
11           word.predicate:want                                    <bos_e>   
12            word.predicate:sin                         word.predicate:say   
13          word.predicate:throw                        word.predicate:pale   
14           word.predicate:know                  ACaseOfIdentity:Windibank   
15         word.predicate:suffer                        word.predicate:call   
16         word.predicate:arrest                        DevilsFoot:Mortimer   
17                       <bos_e>                         CrookedMan:soldier   
18             word.predicate:go                   CrookedMan:Old_Testament   
19        word.predicate:notKnow                       word.predicate:David   

                                      subject                           why  \
0                          CrookedMan:Barclay          CrookedMan:apoplexia   
1                             AllTitle:Holmes             CrookedMan:Davide   
2                           CrookedMan:Davide            word.predicate:die   
3                         DevilsFoot:Mortimer                CrookedMan:371   
4                             AllTitle:Watson                       <bos_e>   
5                            CrookedMan:Nancy          word.predicate:David   
6                    CrookedMan:sin_of_Davide                CrookedMan:373   
7                     AbbeyGrange:Jack_Croker               CrookedMan:363a   
8                                     <bos_e>                CrookedMan:369   
9                            CrookedMan:Henry                CrookedMan:372   
10              AbbeyGrange:Lady_Brackenstall                CrookedMan:359   
11                           CrookedMan:beast                CrookedMan:370   
12  CrookedMan:episode_of_Uriah_and_Bathsheba              CrookedMan:Nancy   
13                        CrookedMan:Morrison                CrookedMan:329   
14                          CrookedMan:police      CrookedMan:Old_Testament   
15                          DancingMen:Cubitt        CrookedMan:living_room   
16                           CrookedMan:Teddy  CrookedMan:preface_of_Samuel   
17                           DancingMen:Elsie              CrookedMan:beast   
18                       word.predicate:exist                CrookedMan:086   
19                        AbbeyGrange:Theresa           word.predicate:pale   

                               what                                      where  
0                 CrookedMan:Davide  CrookedMan:episode_of_Uriah_and_Bathsheba  
1       CrookedMan:same_kind_of_sin                     CrookedMan:living_room  
2      CrookedMan:preface_of_Samuel                   CrookedMan:Old_Testament  
3                  CrookedMan:stick                     CrookedMan:main_street  
4               CrookedMan:criminal                         CrookedMan:curtain  
5   CrookedMan:postscript_of_Samuel                             CrookedMan:box  
6                    CrookedMan:370                           CrookedMan:lodge  
7                  CrookedMan:Teddy         CrookedMan:

319

['CrookedMan:369', 'kgc:where', 'CrookedMan:Old_Testament']

head          relation  \
335        <mask_e>       kgc:subject   
330  CrookedMan:372  kgc:hasPredicate   
333        <mask_e>  kgc:hasPredicate   
309  CrookedMan:368       kgc:subject   
337        <mask_e>          kgc:what   
329  CrookedMan:372       kgc:subject   
317  CrookedMan:369       kgc:subject   
325  CrookedMan:371       kgc:subject   
334        <mask_e>          kgc:whom   
319  CrookedMan:369         kgc:where   
336        <mask_e>           kgc:why   
331  CrookedMan:372         kgc:where   
312  CrookedMan:368          kgc:what   
298  CrookedMan:366       kgc:subject   
321  CrookedMan:370       kgc:subject   
324  CrookedMan:371       kgc:subject   
338        <mask_e>         kgc:where   
294  CrookedMan:365       kgc:subject   
314  CrookedMan:368          kgc:what   
311  CrookedMan:368          kgc:what   

                                          tail  atten_from319  
335                         CrookedMan:Barclay       0.039753  
330                       word.predicate:exist       0.037209  
333                         word.predicate:die       0.032188  
309                            AllTitle:Holmes       0.027793  
337                                   <mask_e>       0.027121  
329                   CrookedMan:sin_of_Davide       0.026187  
317                          CrookedMan:Davide       0.023100  
325                         CrookedMan:Barclay       0.023084  
334                                   <mask_e>       0.022878  
319                   CrookedMan:Old_Testament       0.019280  
336                                   <mask_e>       0.018806  
331  CrookedMan:episode_of_Uriah_and_Bathsheba       0.018705  
312                             CrookedMan:370       0.018579  
298                         CrookedMan:Barclay       0.016836  
321                          CrookedMan:Davide       0.015826  
324                          CrookedMan:Davide       0.014446  
338                                   <mask_e>       0.013651  
294                          CrookedMan:Murphy       0.013624  
314                             CrookedMan:372       0.013316  
311                             CrookedMan:369       0.011214

----------


...

----------


338

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation  \
335        <mask_e>       kgc:subject   
334        <mask_e>          kgc:whom   
337        <mask_e>          kgc:what   
336        <mask_e>           kgc:why   
309  CrookedMan:368       kgc:subject   
325  CrookedMan:371       kgc:subject   
331  CrookedMan:372         kgc:where   
338        <mask_e>         kgc:where   
330  CrookedMan:372  kgc:hasPredicate   
324  CrookedMan:371       kgc:subject   
329  CrookedMan:372       kgc:subject   
333        <mask_e>  kgc:hasPredicate   
312  CrookedMan:368          kgc:what   
314  CrookedMan:368          kgc:what   
315  CrookedMan:368          kgc:what   
322  CrookedMan:370  kgc:hasPredicate   
319  CrookedMan:369         kgc:where   
294  CrookedMan:365       kgc:subject   
321  CrookedMan:370       kgc:subject   
327  CrookedMan:371          kgc:what   

                                          tail  atten_from338  
335                         CrookedMan:Barclay       0.058491  
334                                   <mask_e>       0.043377  
337                                   <mask_e>       0.038459  
336                                   <mask_e>       0.030610  
309                            AllTitle:Holmes       0.030019  
325                         CrookedMan:Barclay       0.029632  
331  CrookedMan:episode_of_Uriah_and_Bathsheba       0.029020  
338                                   <mask_e>       0.027173  
330                       word.predicate:exist       0.025600  
324                          CrookedMan:Davide       0.024088  
329                   CrookedMan:sin_of_Davide       0.021955  
333                         word.predicate:die       0.021411  
312                             CrookedMan:370       0.019906  
314                             CrookedMan:372       0.018530  
315                             CrookedMan:373       0.018361  
322                         word.predicate:sin       0.016534  
319                   CrookedMan:Old_Testament       0.016043  
294                          CrookedMan:Murphy       0.015439  
321                          CrookedMan:Davide       0.014803  
327                CrookedMan:same_kind_of_sin       0.014412

----------


### 僧坊荘園
Who killed Lord Blackenstall? (criminal & explanation)
被害者: Sir_Eustace_Brackenstall
犯人: 
犯行動機: 

In [ ]:
victim = 'AbbeyGrange:Sir_Eustace_Brackenstall'
killer = 'AbbeyGrange:Jack_Croker'
df_ranking_AbbeyGrange, df_attension_AbbeyGrange = make_ranking(
    None, None, KILL, victim, MASK_E, MASK_E, MASK_E, MASK_E)

print(f"{killer}, ranking", df_ranking_AbbeyGrange.index[df_ranking_AbbeyGrange['subject'] == killer].tolist()[0])
display(df_ranking_AbbeyGrange.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_AbbeyGrange)
for i in range(len_):
    display(i, df_attension_AbbeyGrange.iloc[i,:3].tolist())
    display(df_attension_AbbeyGrange.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

AbbeyGrange:Jack_Croker, ranking 14


predicate                                  whom  \
0    word.predicate:testify     SilverBlaze:Night_of_the_incident   
1       word.predicate:kill         SilverBlaze:Inspector_Gregory   
2     word.predicate:wander                    word.predicate:hit   
3    word.predicate:notHave         AbbeyGrange:Lady_Brackenstall   
4        word.predicate:bet              SilverBlaze:John_Straker   
5      word.predicate:bring                word.predicate:testify   
6    word.predicate:suspect                word.predicate:collect   
7      word.predicate:train           SilverBlaze:Fitzroy_Simpson   
8    word.predicate:collect               word.predicate:consider   
9      word.predicate:avoid                    word.predicate:try   
10    word.predicate:become                    word.predicate:say   
11   word.predicate:contain  AbbeyGrange:Sir_Eustace_Brackenstall   
12     word.predicate:fight                  word.predicate:fight   
13    word.predicate:manage              SilverBlaze:Edith_Baxter   
14      word.predicate:gain                    word.predicate:let   
15  word.predicate:consider                   word.predicate:hold   
16       word.predicate:try                SilverBlaze:wilderness   
17     word.predicate:worry                word.predicate:propose   
18       word.predicate:put                word.predicate:takeOut   
19     word.predicate:sleep                   word.predicate:need   

                                      subject  \
0                 SilverBlaze:Fitzroy_Simpson   
1               SilverBlaze:Inspector_Gregory   
2                    SilverBlaze:John_Straker   
3                      SilverBlaze:wilderness   
4            SilverBlaze:Wife_of_John_Straker   
5                    SilverBlaze:Silver_Blaze   
6           SilverBlaze:Night_of_the_incident   
7   SilverBlaze:Complexion_of_Fitzroy_Simpson   
8                                     <bos_e>   
9                     SilverBlaze:Silas_Brown   
10         SilverBlaze:Corpse_of_John_Straker   
11         SilverBlaze:Age_of_Fitzroy_Simpson   
12                         SilverBlaze:People   
13                   SilverBlaze:Edith_Baxter   
14                    AbbeyGrange:Jack_Croker   
15                     word.predicate:testify   
16                AbbeyGrange:The_entire_room   
17                          SilverBlaze:knife   
18                      word.predicate:wander   
19                         word.predicate:say   

                                   why                                  what  \
0          SilverBlaze:Fitzroy_Simpson               SilverBlaze:Thick_stick   
1    SilverBlaze:Night_of_the_incident           SilverBlaze:Fitzroy_Simpson   
2                              <bos_e>              SilverBlaze:Silver_Blaze   
3               SilverBlaze:wilderness                               <bos_e>   
4             SilverBlaze:Silver_Blaze                word.predicate:notHave   
5                    SilverBlaze:Horse                SilverBlaze:wilderness   
6             SilverBlaze:John_Straker                     SilverBlaze:knife   
7                SilverBlaze:In_combat     SilverBlaze:Night_of_the_incident   
8                word.predicate:wander                word.predicate:testify   
9                    SilverBlaze:knife                    word.predicate:say   
10              word.predicate:testify                 word.predicate:wander   
11                     SilverBlaze:191  SilverBlaze:Curry_dish_of_Ned_Hunter   
12       SilverBlaze:Inspector_Gregory                       SilverBlaze:196   
13  SilverBlaze:Age_of_Fitzroy_Simpson     SilverBlaze:Place_of_Silver_Blaze   
14                     SilverBlaze:045                    SilverBlaze:candle   
15                     SilverBlaze:192                    word.predicate:try   
16                  word.predicate:say              SilverBlaze:John_Straker   
17                     SilverBlaze:190                      SilverBlaze:196a   
18                

0

['<bos_e>', '<bos_r>', '<bos_e>']

head          relation                                  tail  \
2  <mask_e>          kgc:whom  AbbeyGrange:Sir_Eustace_Brackenstall   
0   <bos_e>           <bos_r>                               <bos_e>   
5  <mask_e>          kgc:what                              <mask_e>   
4  <mask_e>           kgc:why                              <mask_e>   
6  <mask_e>         kgc:where                              <mask_e>   
3  <mask_e>       kgc:subject                              <mask_e>   
1  <mask_e>  kgc:hasPredicate                   word.predicate:kill   

   atten_from0  
2     0.292831  
0     0.216235  
5     0.138091  
4     0.114180  
6     0.113443  
3     0.074020  
1     0.051201

...

----------


6

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation                                  tail  \
2  <mask_e>          kgc:whom  AbbeyGrange:Sir_Eustace_Brackenstall   
0   <bos_e>           <bos_r>                               <bos_e>   
5  <mask_e>          kgc:what                              <mask_e>   
6  <mask_e>         kgc:where                              <mask_e>   
4  <mask_e>           kgc:why                              <mask_e>   
3  <mask_e>       kgc:subject                              <mask_e>   
1  <mask_e>  kgc:hasPredicate                   word.predicate:kill   

   atten_from6  
2     0.340453  
0     0.307999  
5     0.084369  
6     0.082542  
4     0.067754  
3     0.063642  
1     0.053242

----------


In [ ]:
victim = 'AbbeyGrange:Sir_Eustace_Brackenstall'
df_ranking_AbbeyGrange, df_attension_AbbeyGrange = make_ranking(
    'AbbeyGrange:350', 'AbbeyGrange:413', KILL, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_AbbeyGrange.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_AbbeyGrange)
for i in range(len_-20, len_):
    display(i, df_attension_AbbeyGrange.iloc[i,:3].tolist())
    display(df_attension_AbbeyGrange.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                                   whom  \
0        word.predicate:stand          AbbeyGrange:Lady_Brackenstall   
1    word.predicate:notEscape   AbbeyGrange:Sir_Eustace_Brackenstall   
2     word.predicate:concider  AbbeyGrange:Burglary_team_of_Lewisham   
3   word.predicate:cannotFind                        AllTitle:Holmes   
4      word.predicate:collect                     AbbeyGrange:police   
5         word.predicate:kill                       AbbeyGrange:case   
6    word.predicate:constrain                AbbeyGrange:Jack_Croker   
7     word.predicate:inviteIn                        AllTitle:Watson   
8     word.predicate:canSolve            AbbeyGrange:Stanley_Hopkins   
9       word.predicate:inform                  word.predicate:inform   
10     word.predicate:believe                      AbbeyGrange:truth   
11       word.predicate:worry                    AbbeyGrange:Theresa   
12        word.predicate:drop                                <bos_e>   
13     word.predicate:promise                   AbbeyGrange:Criminal   
14      word.predicate:repeat   AbbeyGrange:Sincerity_of_Jack_Croker   
15       word.predicate:steal                   AbbeyGrange:Sydenham   
16         word.predicate:sit               AbbeyGrange:cord_of_bell   
17     word.predicate:notWant        AbbeyGrange:End_of_cord_of_bell   
18     word.predicate:notHave         AbbeyGrange:Sin_of_Jack_Croker   
19         word.predicate:hit                    AbbeyGrange:Fiction   

                                 subject  \
0                AbbeyGrange:Jack_Croker   
1                     AbbeyGrange:police   
2                        AllTitle:Holmes   
3          AbbeyGrange:Lady_Brackenstall   
4                       AbbeyGrange:case   
5        AbbeyGrange:Voice_of_the_people   
6                                <bos_e>   
7                 word.predicate:believe   
8            AbbeyGrange:Stanley_Hopkins   
9   AbbeyGrange:Sir_Eustace_Brackenstall   
10                  AbbeyGrange:everyone   
11                       AllTitle:Watson   
12   AbbeyGrange:Behavior_of_Jack_Croker   
13                       AbbeyGrange:409   
14                   AbbeyGrange:acrobat   
15                   AbbeyGrange:Theresa   
16        AbbeyGrange:Sin_of_Jack_Croker   
17            ACaseOfIdentity:Sutherland   
18       AbbeyGrange:False_charge_person   
19                word.predicate:beClear   

                                        why  \
0                           AbbeyGrange:404   
1                           AbbeyGrange:403   
2                           AbbeyGrange:392   
3                           AbbeyGrange:343   
4               AbbeyGrange:Silver_Products   
5                           AbbeyGrange:386   
6                           AbbeyGrange:375   
7                    AbbeyGrange:accomplice   
8                        AbbeyGrange:police   
9                           AbbeyGrange:409   
10                  AbbeyGrange:Jack_Croker   
11                                  <bos_e>   
12  ACaseOfIdentity:Between_seams_of_window   
13                 word.predicate:notEscape   
14                          AbbeyGrange:389   
15                  word.predicate:concider   
16                          AllTitle:Holmes   
17              word.predicate:Voice_of_God   
18                   word.predicate:believe   
19                          AbbeyGrange:338   

                                    what  \
0                        AbbeyGrange:sin   
1                AbbeyGrange:Jack_Croker   
2                      AbbeyGrange:truth   
3                        AbbeyGrange:409   
4                        AllTitle:Holmes   
5                 AbbeyGrange:appearance   
6   AbbeyGrange:Sincerity_of_Jack_Croker   
7        AbbeyGrange:False_charge_person   
8                    ACaseOfIdentity:hat   
9                     AbbeyGrange:police   
10        AbbeyGrange:Sin_of_Jack_Croker   
11                 AbbeyGrange:Situation   
12                Abbe

264

['AbbeyGrange:410', 'kgc:hasPredicate', 'word.predicate:say']

head     relation                             tail  \
277          <bos_e>      <bos_r>                          <bos_e>   
266          <bos_e>      <bos_r>                          <bos_e>   
259          <bos_e>      <bos_r>                          <bos_e>   
262          <bos_e>      <bos_r>                          <bos_e>   
270          <bos_e>      <bos_r>                          <bos_e>   
273          <bos_e>      <bos_r>                          <bos_e>   
254          <bos_e>      <bos_r>                          <bos_e>   
249          <bos_e>      <bos_r>                          <bos_e>   
245          <bos_e>      <bos_r>                          <bos_e>   
267  AbbeyGrange:411  kgc:subject          AbbeyGrange:Jack_Croker   
241          <bos_e>      <bos_r>                          <bos_e>   
236          <bos_e>      <bos_r>                          <bos_e>   
258  AbbeyGrange:408       kgc:to                  AllTitle:Watson   
271  AbbeyGrange:412  kgc:subject  AbbeyGrange:Voice_of_the_people   
263  AbbeyGrange:410  kgc:subject                  AllTitle:Watson   
283         <mask_e>    kgc:where                         <mask_e>   
231          <bos_e>      <bos_r>                          <bos_e>   
274  AbbeyGrange:413  kgc:subject          AbbeyGrange:Jack_Croker   
228          <bos_e>      <bos_r>                          <bos_e>   
281         <mask_e>      kgc:why                         <mask_e>   

     atten_from264  
277       0.035200  
266       0.035114  
259       0.035062  
262       0.034613  
270       0.034092  
273       0.030823  
254       0.029809  
249       0.028509  
245       0.021990  
267       0.020085  
241       0.019926  
236       0.018181  
258       0.015804  
271       0.015388  
263       0.015030  
283       0.014442  
231       0.013854  
274       0.012991  
228       0.012967  
281       0.012102

----------


...

----------


283

['<mask_e>', 'kgc:where', '<mask_e>']

head     relation                                  tail  \
274  AbbeyGrange:413  kgc:subject               AbbeyGrange:Jack_Croker   
267  AbbeyGrange:411  kgc:subject               AbbeyGrange:Jack_Croker   
279         <mask_e>     kgc:whom  AbbeyGrange:Sir_Eustace_Brackenstall   
276  AbbeyGrange:413     kgc:what                       AllTitle:Holmes   
282         <mask_e>     kgc:what                              <mask_e>   
263  AbbeyGrange:410  kgc:subject                       AllTitle:Watson   
283         <mask_e>    kgc:where                              <mask_e>   
269  AbbeyGrange:411     kgc:what                       AbbeyGrange:sin   
277          <bos_e>      <bos_r>                               <bos_e>   
270          <bos_e>      <bos_r>                               <bos_e>   
257  AbbeyGrange:408     kgc:what        AbbeyGrange:Sin_of_Jack_Croker   
258  AbbeyGrange:408       kgc:to                       AllTitle:Watson   
265  AbbeyGrange:410     kgc:what                       AbbeyGrange:409   
281         <mask_e>      kgc:why                              <mask_e>   
271  AbbeyGrange:412  kgc:subject       AbbeyGrange:Voice_of_the_people   
280         <mask_e>  kgc:subject                              <mask_e>   
266          <bos_e>      <bos_r>                               <bos_e>   
273          <bos_e>      <bos_r>                               <bos_e>   
260  AbbeyGrange:409  kgc:subject               AbbeyGrange:Jack_Croker   
254          <bos_e>      <bos_r>                               <bos_e>   

     atten_from283  
274       0.050374  
267       0.045212  
279       0.042270  
276       0.028692  
282       0.025086  
263       0.023401  
283       0.021338  
269       0.021310  
277       0.019092  
270       0.018190  
257       0.017750  
258       0.017742  
265       0.017694  
281       0.017657  
271       0.017389  
280       0.016586  
266       0.015865  
273       0.015671  
260       0.015237  
254       0.015092

----------


### 入院患者
Who killed Blessington? (criminal & explanation)
被害者: Blessington
犯人: 3人
犯行動機: 

In [ ]:
victim = 'ResidentPatient:Blessington'
df_ranking_Blessington, df_attension_Blessington = make_ranking(
    'ResidentPatient:250', 'ResidentPatient:323', KILL, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_Blessington.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_Blessington)
for i in range(len_-20, len_):
    display(i, df_attension_Blessington.iloc[i,:3].tolist())
    display(df_attension_Blessington.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate  \
0          word.predicate:kill   
1         word.predicate:catch   
2   word.predicate:leaveBehind   
3        word.predicate:escape   
4          word.predicate:fail   
5        word.predicate:reveal   
6          word.predicate:lock   
7        word.predicate:betray   
8         word.predicate:stand   
9          word.predicate:gain   
10         word.predicate:hide   
11      word.predicate:revenge   
12   word.predicate:cannotFind   
13         word.predicate:stop   
14        word.predicate:bring   
15          word.predicate:bet   
16          word.predicate:cut   
17          word.predicate:use   
18         word.predicate:fear   
19          word.predicate:try   

                                                 whom  \
0                         ResidentPatient:Blessington   
1                  ResidentPatient:Moderator_of_Tobin   
2                          ResidentPatient:Helper_boy   
3                     ResidentPatient:Percy_Trevelyan   
4                       AbbeyGrange:Lady_Brackenstall   
5                            SilverBlaze:Silver_Blaze   
6                                     AllTitle:Holmes   
7                           ResidentPatient:Young_man   
8                         ResidentPatient:Elderly_man   
9                          ACaseOfIdentity:Sutherland   
10                            SilverBlaze:Silas_Brown   
11                          SilverBlaze:King_s_Pyland   
12                           SilverBlaze:John_Straker   
13                               AbbeyGrange:Criminal   
14                                   CrookedMan:Nancy   
15                                            <bos_e>   
16  ResidentPatient:Evidence_of_the_major_events_o...   
17                              SilverBlaze:Wasteland   
18                           SilverBlaze:Edith_Baxter   
19                                 SilverBlaze:People   

                                              subject  \
0                         ResidentPatient:Blessington   
1                         ResidentPatient:Elderly_man   
2                           ResidentPatient:Young_man   
3                          ResidentPatient:Helper_boy   
4                     ResidentPatient:Percy_Trevelyan   
5                                ResidentPatient:319a   
6                  SilverBlaze:Murder_of_John_Straker   
7                                  SilverBlaze:People   
8                                             <bos_e>   
9                          ResidentPatient:Cartwright   
10  ResidentPatient:Evidence_of_the_major_events_o...   
11                             ResidentPatient:police   
12                                SilverBlaze:Isonomy   
13           ResidentPatient:Worthington_bank_Robbers   
14                                    AllTitle:Holmes   
15                           SilverBlaze:John_Straker   
16                           SilverBlaze:Silver_Blaze   
17          SilverBlaze:Disappearance_of_Silver_Blaze   
18                        ResidentPatient:Source_Date   
19    ResidentPatient:Major_event_of_Worthingdon_bank   

                                                  why  \
0                                             <bos_e>   
1                                    SilverBlaze:018a   
2                                ResidentPatient:319a   
3                          ResidentPatient:Helper_boy   
4                         ResidentPatient:Blessington   
5                                 word.predicate:free   
6                           ResidentPatient:Young_man   
7                    ResidentPatient:Blessington_room   
8                         ResidentPatient:Elderly_man   
9                     ResidentPatient:Percy_Trevelyan   
10                             word.predicate:clearly   
11                             word.predicate:succeed   
12                               ResidentPatient:Obex   
13                               word.predicate:hefty   
14                      word.predicate:five_years_old  

375

['ResidentPatient:320', 'kgc:hasPredicate', 'word.predicate:fail']

head     relation                         tail  \
384               <bos_e>      <bos_r>                      <bos_e>   
380               <bos_e>      <bos_r>                      <bos_e>   
388               <bos_e>      <bos_r>                      <bos_e>   
376               <bos_e>      <bos_r>                      <bos_e>   
373               <bos_e>      <bos_r>                      <bos_e>   
361               <bos_e>      <bos_r>                      <bos_e>   
367               <bos_e>      <bos_r>                      <bos_e>   
336               <bos_e>      <bos_r>                      <bos_e>   
356               <bos_e>      <bos_r>                      <bos_e>   
346               <bos_e>      <bos_r>                      <bos_e>   
332               <bos_e>      <bos_r>                      <bos_e>   
342               <bos_e>      <bos_r>                      <bos_e>   
350               <bos_e>      <bos_r>                      <bos_e>   
362   ResidentPatient:319  kgc:subject  ResidentPatient:Elderly_man   
339               <bos_e>      <bos_r>                      <bos_e>   
363   ResidentPatient:319  kgc:subject    ResidentPatient:Young_man   
328               <bos_e>      <bos_r>                      <bos_e>   
385   ResidentPatient:323  kgc:subject  ResidentPatient:Blessington   
381   ResidentPatient:322  kgc:subject  ResidentPatient:Blessington   
368  ResidentPatient:319a  kgc:subject  ResidentPatient:Elderly_man   

     atten_from375  
384       0.035150  
380       0.033458  
388       0.032763  
376       0.031401  
373       0.029093  
361       0.025119  
367       0.025004  
336       0.021143  
356       0.020062  
346       0.018407  
332       0.017564  
342       0.016974  
350       0.016953  
362       0.016915  
339       0.016834  
363       0.016372  
328       0.016101  
385       0.015457  
381       0.014980  
368       0.014801

----------


...

----------


394

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation  \
385   ResidentPatient:323       kgc:subject   
393              <mask_e>          kgc:what   
369  ResidentPatient:319a       kgc:subject   
387   ResidentPatient:323          kgc:what   
390              <mask_e>          kgc:whom   
379   ResidentPatient:321          kgc:when   
368  ResidentPatient:319a       kgc:subject   
381   ResidentPatient:322       kgc:subject   
391              <mask_e>       kgc:subject   
389              <mask_e>  kgc:hasPredicate   
362   ResidentPatient:319       kgc:subject   
388               <bos_e>           <bos_r>   
394              <mask_e>         kgc:where   
366   ResidentPatient:319          kgc:what   
384               <bos_e>           <bos_r>   
363   ResidentPatient:319       kgc:subject   
383   ResidentPatient:322          kgc:what   
386   ResidentPatient:323   kgc:hasProperty   
382   ResidentPatient:322   kgc:hasProperty   
370  ResidentPatient:319a       kgc:subject   

                                                  tail  atten_from394  
385                        ResidentPatient:Blessington       0.031190  
393                                           <mask_e>       0.025837  
369                          ResidentPatient:Young_man       0.025742  
387  ResidentPatient:The_strength_of_the_fellow_rev...       0.025504  
390                        ResidentPatient:Blessington       0.025346  
379                         ResidentPatient:third_time       0.022435  
368                        ResidentPatient:Elderly_man       0.021974  
381                        ResidentPatient:Blessington       0.021254  
391                                           <mask_e>       0.020154  
389                                word.predicate:kill       0.019844  
362                        ResidentPatient:Elderly_man       0.019526  
388                                            <bos_e>       0.018729  
394                                           <mask_e>       0.018022  
366                               ResidentPatient:319a       0.017982  
384                                            <bos_e>       0.017708  
363                          ResidentPatient:Young_man       0.017545  
383                        ResidentPatient:Source_Date       0.017422  
386                                word.predicate:know       0.015956  
382                                word.predicate:know       0.015779  
370                         ResidentPatient:Helper_boy       0.015648

----------


### 白銀
Who took out the White Silver Blaze? (criminal & explanation) 
被害者: Silver_Blaze
犯人: 
犯行動機: 

In [ ]:
victim = 'SilverBlaze:Silver_Blaze'
df_ranking_SilverBlaze, df_attension_SilverBlaze = make_ranking(
    'SilverBlaze:330', 'SilverBlaze:396', BRING, MASK_E, MASK_E, MASK_E, victim, MASK_E)

display(df_ranking_SilverBlaze.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_SilverBlaze)
for i in range(len_-20, len_):
    display(i, df_attension_SilverBlaze.iloc[i,:3].tolist())
    display(df_attension_SilverBlaze.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                                whom  \
0       word.predicate:bring            SilverBlaze:Silver_Blaze   
1        word.predicate:give                     AllTitle:Holmes   
2        word.predicate:drop       SilverBlaze:Inspector_Gregory   
3         word.predicate:get            SilverBlaze:John_Straker   
4     word.predicate:notHave            SilverBlaze:Colonel_Ross   
5       word.predicate:smash               SilverBlaze:Wasteland   
6         word.predicate:buy                  word.predicate:let   
7       word.predicate:carry  SilverBlaze:Photos_of_John_Straker   
8        word.predicate:pick                     SilverBlaze:394   
9        word.predicate:fire                  word.predicate:ask   
10    word.predicate:suspect         SilverBlaze:Fitzroy_Simpson   
11    word.predicate:notBark       SilverBlaze:Surgery_of_tendon   
12    word.predicate:comeOut                     AllTitle:Watson   
13        word.predicate:try      SilverBlaze:Place_of_the_horse   
14  word.predicate:canDecide                    SilverBlaze:331a   
15  word.predicate:cultivate                             <bos_e>   
16      word.predicate:catch                     SilverBlaze:335   
17        word.predicate:ask                     SilverBlaze:328   
18         word.predicate:go              word.predicate:prepare   
19       word.predicate:kill   SilverBlaze:thigh_of_John_Straker   

                                    subject  \
0                           AllTitle:Holmes   
1                  SilverBlaze:Colonel_Ross   
2                  SilverBlaze:John_Straker   
3                  SilverBlaze:Silver_Blaze   
4             SilverBlaze:Inspector_Gregory   
5          SilverBlaze:Youth_stables_number   
6                       SilverBlaze:3_sheep   
7                   SilverBlaze:Brown_horse   
8                   SilverBlaze:Silas_Brown   
9           SilverBlaze:legs_of_brown_horse   
10              SilverBlaze:Fitzroy_Simpson   
11                          AllTitle:Watson   
12         SilverBlaze:Wife_of_John_Straker   
13                       SilverBlaze:People   
14  SilverBlaze:Subordinates_of_Silas_Brown   
15          SilverBlaze:Face_of_brown_horse   
16       SilverBlaze:Jockey_of_Colonel_Ross   
17           SilverBlaze:Place_of_the_horse   
18       SilverBlaze:Corpse_of_John_Straker   
19                SilverBlaze:Injured_horse   

                                   why                                 what  \
0                      SilverBlaze:394             SilverBlaze:Silver_Blaze   
1                      SilverBlaze:375   SilverBlaze:Photos_of_John_Straker   
2             SilverBlaze:Silver_Blaze                      SilverBlaze:325   
3                      SilverBlaze:385                      SilverBlaze:337   
4           SilverBlaze:white_forehead                     SilverBlaze:331a   
5                      SilverBlaze:379                      SilverBlaze:328   
6       SilverBlaze:Brown_Umanoashi_of                      SilverBlaze:335   
7                     SilverBlaze:387a                     SilverBlaze:Work   
8                      SilverBlaze:241    SilverBlaze:How_to_escape_the_sin   
9                      SilverBlaze:377        SilverBlaze:Accident_of_sheep   
10                    SilverBlaze:342a                      AllTitle:Holmes   
11                     SilverBlaze:365                      SilverBlaze:tie   
12                     SilverBlaze:356                      SilverBlaze:305   
13  SilverBlaze:Photos_of_John_Straker  SilverBlaze:the_hat_decoration_shop   
14                     SilverBlaze:363                      SilverBlaze:sin   
15                     SilverBlaze:335                      SilverBlaze:346   
16                     SilverBlaze:242         SilverBlaze:Ready_for_jockey   
17                             <bos_e>                      SilverBlaze:349   
18                     SilverBlaze:362                      SilverBlaze:342   
19                    

363

['SilverBlaze:394', 'kgc:subject', 'SilverBlaze:John_Straker']

head          relation                            tail  \
363   SilverBlaze:394       kgc:subject        SilverBlaze:John_Straker   
368   SilverBlaze:395  kgc:hasPredicate             word.predicate:have   
379          <mask_e>       kgc:subject                        <mask_e>   
381          <mask_e>          kgc:what        SilverBlaze:Silver_Blaze   
365   SilverBlaze:394          kgc:what   SilverBlaze:Expensive_clothes   
375   SilverBlaze:396            kgc:to                 AllTitle:Holmes   
340   SilverBlaze:390  kgc:hasPredicate             word.predicate:fall   
352   SilverBlaze:392  kgc:hasPredicate         word.predicate:practice   
380          <mask_e>           kgc:why                        <mask_e>   
339   SilverBlaze:390       kgc:subject        SilverBlaze:John_Straker   
378          <mask_e>          kgc:whom                        <mask_e>   
355   SilverBlaze:393       kgc:subject                 AllTitle:Holmes   
353   SilverBlaze:392          kgc:what   SilverBlaze:Surgery_of_tendon   
367   SilverBlaze:395       kgc:subject        SilverBlaze:John_Straker   
369   SilverBlaze:395          kgc:what                SilverBlaze:debt   
361  SilverBlaze:393a          kgc:what                 SilverBlaze:394   
382          <mask_e>         kgc:where                        <mask_e>   
374   SilverBlaze:396          kgc:what  SilverBlaze:Place_of_the_horse   
351   SilverBlaze:392       kgc:subject        SilverBlaze:John_Straker   
364   SilverBlaze:394  kgc:hasPredicate              word.predicate:buy   

     atten_from363  
363       0.039282  
368       0.034252  
379       0.029990  
381       0.026872  
365       0.026018  
375       0.022384  
340       0.021835  
352       0.020858  
380       0.019974  
339       0.019240  
378       0.019228  
355       0.019190  
353       0.018835  
367       0.018590  
369       0.018401  
361       0.018285  
382       0.018265  
374       0.018138  
351       0.017817  
364       0.017228

----------


...

----------


382

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation                            tail  \
363   SilverBlaze:394       kgc:subject        SilverBlaze:John_Straker   
379          <mask_e>       kgc:subject                        <mask_e>   
367   SilverBlaze:395       kgc:subject        SilverBlaze:John_Straker   
351   SilverBlaze:392       kgc:subject        SilverBlaze:John_Straker   
381          <mask_e>          kgc:what        SilverBlaze:Silver_Blaze   
339   SilverBlaze:390       kgc:subject        SilverBlaze:John_Straker   
375   SilverBlaze:396            kgc:to                 AllTitle:Holmes   
378          <mask_e>          kgc:whom                        <mask_e>   
342  SilverBlaze:390a       kgc:subject        SilverBlaze:John_Straker   
374   SilverBlaze:396          kgc:what  SilverBlaze:Place_of_the_horse   
372   SilverBlaze:396       kgc:subject        SilverBlaze:Colonel_Ross   
382          <mask_e>         kgc:where                        <mask_e>   
346   SilverBlaze:391       kgc:subject        SilverBlaze:John_Straker   
359  SilverBlaze:393a       kgc:subject                 AllTitle:Holmes   
355   SilverBlaze:393       kgc:subject                 AllTitle:Holmes   
380          <mask_e>           kgc:why                        <mask_e>   
370   SilverBlaze:395           kgc:why                 SilverBlaze:394   
361  SilverBlaze:393a          kgc:what                 SilverBlaze:394   
365   SilverBlaze:394          kgc:what   SilverBlaze:Expensive_clothes   
377          <mask_e>  kgc:hasPredicate            word.predicate:bring   

     atten_from382  
363       0.077649  
379       0.048823  
367       0.043226  
351       0.037057  
381       0.036339  
339       0.028160  
375       0.026920  
378       0.025507  
342       0.025033  
374       0.023467  
372       0.022099  
382       0.021661  
346       0.020175  
359       0.019123  
355       0.018937  
380       0.017573  
370       0.016443  
361       0.014848  
365       0.014536  
377       0.013947

----------


### 花嫁失踪事件（同一事件）
hozmaの失踪の名瀬を探る
被害者: ACaseOfIdentity:Hozma
犯人: 
犯行動機: 

In [ ]:
victim = 'ACaseOfIdentity:Hosmer'
df_ranking_ACaseOfIdentity, df_attension_ACaseOfIdentity = make_ranking(
    'ACaseOfIdentity:510', 'ACaseOfIdentity:578', HIDE, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_ACaseOfIdentity.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_ACaseOfIdentity)
for i in range(len_-20, len_):
    display(i, df_attension_ACaseOfIdentity.iloc[i,:3].tolist())
    display(df_attension_ACaseOfIdentity.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")


predicate                                           whom  \
0          word.predicate:know                         ACaseOfIdentity:Hosmer   
1           word.predicate:see                     ACaseOfIdentity:Sutherland   
2            word.predicate:go                      ACaseOfIdentity:Windibank   
3   word.predicate:cannotSleep                                AllTitle:Holmes   
4      word.predicate:beTypeed                               CrookedMan:Nancy   
5       word.predicate:believe                                AllTitle:Watson   
6          word.predicate:have                       SilverBlaze:John_Straker   
7          word.predicate:want           ACaseOfIdentity:mother_of_Sutherland   
8       word.predicate:notWant                          ACaseOfIdentity:Hardy   
9        word.predicate:happen             ACaseOfIdentity:Personal_statement   
10          word.predicate:cry                              DevilsFoot:George   
11       word.predicate:notice                ACaseOfIdentity:hansom_carriage   
12       word.predicate:repeat                  SilverBlaze:Inspector_Gregory   
13      word.predicate:jumpOut                ACaseOfIdentity:feature_of_type   
14        word.predicate:goOut                       ACaseOfIdentity:Solution   
15          word.predicate:say                       SilverBlaze:Silver_Blaze   
16        word.predicate:match  ACaseOfIdentity:Treatment_of_serious_patients   
17       word.predicate:arrive                              DevilsFoot:Brenda   
18      word.predicate:notKnow                        SilverBlaze:Silas_Brown   
19         word.predicate:hear                                DevilsFoot:Owen   

                                     subject                             why  \
0                 ACaseOfIdentity:Sutherland           ACaseOfIdentity:money   
1                     ACaseOfIdentity:Hosmer  ACaseOfIdentity:Assault_threat   
2                  ACaseOfIdentity:Windibank       ACaseOfIdentity:Illegally   
3                            AllTitle:Holmes                         <bos_e>   
4                      ACaseOfIdentity:reply       ACaseOfIdentity:Windibank   
5            ACaseOfIdentity:feature_of_type             word.predicate:want   
6                                    <bos_e>           word.predicate:typist   
7                    ACaseOfIdentity:company         word.predicate:canSolve   
8                            AllTitle:Watson               word.predicate:go   
9         ACaseOfIdentity:Personal_statement        word.predicate:notAppear   
10                  ACaseOfIdentity:disguise              word.predicate:say   
11                        word.predicate:say          ACaseOfIdentity:Hosmer   
12                        CrookedMan:Barclay           word.predicate:remove   
13                          CrookedMan:Henry           word.predicate:keepUp   
14     ACaseOfIdentity:brother_of_Sutherland     CrookedMan:Indian_Rebellion   
15  ACaseOfIdentity:handwriting_of_Windibank                  CrookedMan:329   
16      ACaseOfIdentity:mother_of_Sutherland           word.predicate:canSue   
17                       word.predicate:want                 AbbeyGrange:404   
18      ACaseOfIdentity:friend_of_Sutherland             word.predicate:send   
19                       ACaseOfIdentity:law             ACaseOfIdentity:547   

                                        what  \
0                     ACaseOfIdentity:Hosmer   
1                  ACaseOfIdentity:Windibank   
2   ACaseOfIdentity:handwriting_of_Windibank   
3                 ACaseOfIdentity:Sutherland   
4                    ACaseOfIdentity:glasses   
5                       ACaseOfIdentity:Moth   
6                      ACaseOfIdentity:voice   
7                      ACaseOfIdentity:money   
8              ACaseOfIdentity:Color_glasses   
9                     ACaseOfIdentity:letter   
10                ACaseOfIdentity:With_voice   
11                     ACaseOfIdentity:truth   
12            

303

['ACaseOfIdentity:575', 'kgc:what', 'ACaseOfIdentity:Hosmer']

head          relation  \
302  ACaseOfIdentity:575  kgc:hasPredicate   
301  ACaseOfIdentity:575       kgc:subject   
303  ACaseOfIdentity:575          kgc:what   
305  ACaseOfIdentity:576       kgc:subject   
319             <mask_e>       kgc:subject   
282  ACaseOfIdentity:570          kgc:from   
309  ACaseOfIdentity:577       kgc:subject   
317             <mask_e>  kgc:hasPredicate   
322             <mask_e>         kgc:where   
281  ACaseOfIdentity:570          kgc:what   
298  ACaseOfIdentity:574       kgc:subject   
313  ACaseOfIdentity:578       kgc:subject   
318             <mask_e>          kgc:whom   
299  ACaseOfIdentity:574   kgc:hasProperty   
310  ACaseOfIdentity:577   kgc:hasProperty   
293  ACaseOfIdentity:573       kgc:subject   
296  ACaseOfIdentity:573          kgc:whom   
291  ACaseOfIdentity:572          kgc:what   
275  ACaseOfIdentity:569          kgc:what   
320             <mask_e>           kgc:why   

                                        tail  atten_from303  
302                     word.predicate:match       0.116927  
301          ACaseOfIdentity:feature_of_type       0.041648  
303                   ACaseOfIdentity:Hosmer       0.034078  
305                  ACaseOfIdentity:company       0.024203  
319                                 <mask_e>       0.023159  
282       ACaseOfIdentity:Personal_statement       0.023116  
309       ACaseOfIdentity:Personal_statement       0.022063  
317                      word.predicate:hide       0.020441  
322                                 <mask_e>       0.019928  
281                    ACaseOfIdentity:voice       0.017806  
298                    ACaseOfIdentity:reply       0.017384  
313               ACaseOfIdentity:Sutherland       0.016764  
318                   ACaseOfIdentity:Hosmer       0.016081  
299                    word.predicate:typist       0.015699  
310                        word.predicate:is       0.015622  
293                          AllTitle:Holmes       0.015572  
296                ACaseOfIdentity:Windibank       0.014199  
291  ACaseOfIdentity:characteristics_of_type       0.012428  
275     ACaseOfIdentity:company_of_Windibank       0.011784  
320                                 <mask_e>       0.011333

----------


...

----------


322

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation  \
301  ACaseOfIdentity:575       kgc:subject   
305  ACaseOfIdentity:576       kgc:subject   
319             <mask_e>       kgc:subject   
318             <mask_e>          kgc:whom   
313  ACaseOfIdentity:578       kgc:subject   
298  ACaseOfIdentity:574       kgc:subject   
309  ACaseOfIdentity:577       kgc:subject   
321             <mask_e>          kgc:what   
322             <mask_e>         kgc:where   
317             <mask_e>  kgc:hasPredicate   
320             <mask_e>           kgc:why   
311  ACaseOfIdentity:577          kgc:what   
314  ACaseOfIdentity:578  kgc:hasPredicate   
296  ACaseOfIdentity:573          kgc:whom   
252  ACaseOfIdentity:563       kgc:subject   
310  ACaseOfIdentity:577   kgc:hasProperty   
293  ACaseOfIdentity:573       kgc:subject   
315  ACaseOfIdentity:578          kgc:what   
307  ACaseOfIdentity:576          kgc:what   
303  ACaseOfIdentity:575          kgc:what   

                                   tail  atten_from322  
301     ACaseOfIdentity:feature_of_type       0.056671  
305             ACaseOfIdentity:company       0.055875  
319                            <mask_e>       0.055015  
318              ACaseOfIdentity:Hosmer       0.054688  
313          ACaseOfIdentity:Sutherland       0.052709  
298               ACaseOfIdentity:reply       0.046229  
309  ACaseOfIdentity:Personal_statement       0.039633  
321                            <mask_e>       0.038679  
322                            <mask_e>       0.037073  
317                 word.predicate:hide       0.033318  
320                            <mask_e>       0.032257  
311           ACaseOfIdentity:Windibank       0.028194  
314           word.predicate:notBelieve       0.022506  
296           ACaseOfIdentity:Windibank       0.020370  
252           ACaseOfIdentity:Windibank       0.017690  
310                   word.predicate:is       0.016994  
293                     AllTitle:Holmes       0.016915  
315                     AllTitle:Holmes       0.016171  
307                 ACaseOfIdentity:577       0.015101  
303              ACaseOfIdentity:Hosmer       0.013687

----------
